In [1]:
%matplotlib qt
# Linear regression


In [2]:
import matplotlib as mpl
import happi
import numpy as np
import matplotlib.pyplot as plt

jetcmap = plt.cm.get_cmap("jet", 9) #generate a jet map with 10 values "rainbow", "jet", YlOrRd
jet_vals = jetcmap(np.arange(9)) #extract those values as an array 
jet_vals[0] = [1.0, 1, 1.0, 1] #change the first value 
jet_vals[8] = [0.0, 0, 0.0, 1] #change the first value 
newcmap = mpl.colors.LinearSegmentedColormap.from_list("mine", jet_vals) 

# plt.rc('font', family='sans-serif', serif='Arial')
# plt.rc('text', usetex=False)
# plt.rc('xtick', labelsize=13)
# plt.rc('ytick', labelsize=13)
# plt.rc('axes', labelsize=13)
# plt.rc('legend', fontsize=10)

from matplotlib import font_manager

font_dirs = ['/Users/yao/Documents/Calibri and Cambria Fonts/']
font_files = font_manager.findSystemFonts(fontpaths=font_dirs)

for font_file in font_files:
    font_manager.fontManager.addfont(font_file)

# set font
plt.rcParams['font.family'] = 'Calibri'

plt.rc('text', usetex=False)
plt.rc('xtick', labelsize=14)
plt.rc('ytick', labelsize=14)
plt.rc('axes', labelsize=14)
plt.rc('legend', fontsize=12)

/var/folders/2t/97rc3fl92tg15k2l_4sk5hsh0000gn/T/ipykernel_83117/710648007.py:6: MatplotlibDeprecationWarning: The get_cmap function was deprecated in Matplotlib 3.7 and will be removed two minor releases later. Use ``matplotlib.colormaps[name]`` or ``matplotlib.colormaps.get_cmap(obj)`` instead.
  jetcmap = plt.cm.get_cmap("jet", 9) #generate a jet map with 10 values "rainbow", "jet", YlOrRd


In [3]:
wkdir = [
    # '/Users/yao/Desktop/Data/apo_sp_t0/' # test 0
    # '/Users/yao/Desktop/Data/apo_sp_t1/' # test 1
    '/Users/yao/Desktop/Data/apo_sp_t2/' # test 2
    ]

In [4]:
S0 = happi.Open(wkdir[0], reference_angular_frequency_SI = 56375055300167.87)
# S1 = happi.Open(wkdir[1], reference_angular_frequency_SI = 56375055300167.87)
# S2 = happi.Open(wkdir[2], reference_angular_frequency_SI = 56375055300167.87)

Loaded simulation '/Users/yao/Desktop/Data/apo_sp_t2/'
Scanning for Scalar diagnostics
Scanning for Field diagnostics
Scanning for Probe diagnostics
Scanning for ParticleBinning diagnostics
Scanning for RadiationSpectrum diagnostics
Scanning for Performance diagnostics
Scanning for Screen diagnostics
Scanning for Tracked particle diagnostics
Scanning for new particle diagnostics


In [5]:
# prepare constants, units

me = 9.1e-31
mp = 1836.*me
qe = 1.6e-19
ep = 8.9e-12  # epsilon_0
c  = 3.0e8
wr = S0.namelist.w_r
de = c / wr
Lx = S0.namelist.L_x.real * de * 1e3      # in mm
dx = S0.namelist.d_x * de * 1e3           # in mm

Te = S0.namelist.T_e * 511.e3             # in eV
ne = 1.0e18                              # in cm-3
ld = 7.43e2 * Te**0.5 * ne**(-0.5) * 10. # in mm
dt = S0.namelist.d_t

B0 = S0.namelist.B_z * (me * wr / qe)
wc = qe * B0 / me

In [6]:
def get_wr(ne):
    # ne: the electron density in cm^-3
    return np.sqrt(ne*1e6 * qe**2 / (me * ep))

print('wr =', get_wr(3e18) )

wr = 97378910341415.27


In [7]:
# quick check about the process
S0.ParticleBinning(0,
                   units=['MeV','ns','mm','1e3 km/s'],
                   data_log=True,
                   color='blue',
                   linestyle='--',
                   cmap=newcmap,
                   vmin=-2,
                   vmax=4,
                   ymin=-35,
                   ymax=35,
                #    sum={'x':'all'}
                   ).slide()


#0 - Number density of species # 0,2,4
    x from 0 to 4096 in 500 steps 
    vx from -0.5 to 0.5 in 500 steps 

The value in each bin is the sum of the `deposited_quantity` divided by the bin size



/Users/yao/Smilei/happi/_Diagnostics/Diagnostic.py:857: RuntimeWarning: divide by zero encountered in log10
  return self._np.log10( self._dataLinAtTime(t) )


2025-03-06 10:57:41.906 Python[83117:11090233] +[IMKClient subclass]: chose IMKClient_Modern
2025-03-06 10:57:41.906 Python[83117:11090233] +[IMKInputSession subclass]: chose IMKInputSession_Modern


In [9]:
# quick check about the process
S0.ParticleBinning(2,
                   units=['MeV','ns','mm','1e3 km/s'],
                   data_log=True,
                   color='blue',
                #    linestyle='--',
                   cmap=newcmap,
                #    vmin=-2,
                #    vmax=4,
                  #  ymin=-35,
                  #  ymax=35,
                   sum={'x':'all'}
                   ).slide()


#2 - Number density of species # 0,2,4
    x from 0 to 4096 in 500 steps 
    ekin from 0 to 30 in 500 steps 

average for all x
The value in each bin is the sum of the `deposited_quantity` divided by the bin size



In [8]:
# Function for spectrum

def spect_load_1d(wkdir,time,species,xmin,xmax):
    """
    Inputs ----
    wkdir      : string, data directory
    time       : float,  [0,1] of the time_end 
    species    : int,    which species you want to plot
                         according to your own diagnostic in the Namelist
    xmin, xmax : float,  spatial selections, NOTE: in unit of de
    
    Outputs ---
    ekin       : float,  x-axis, energy(E) in MeV
    num        : float,  y-axis, E \frac{dN}{dE} \frac{1}{N}
                                 N  is the total number of particles
                                 dN is the number of particles in each energy range (dE)
                                 dE is the energy range
    simu_time  : float,  simulation time
    """
    S = happi.Open(wkdir)                        # No need to open the data again.
    dt = S.namelist.d_t                            # get simulation timestep
    ts = S.ParticleBinning(species).getTimesteps() # get all the timesteps available for this diag.
    iteration = int(ts[-2] * time)                 # choose the time you want by a factor of [0,1]*T_end
    simu_time = iteration * dt / wr                # convert it into real unit
    pb = S.ParticleBinning(species).get(iteration) # get the diag. data from the chosen timestep
    
    xx   = pb['x'] * de * 1e3                      # get position information and convert the unit to mm
    ekin = pb['ekin'] * 0.511                      # get energy information (E) and convert the unit to MeV -- the x-axis
    data = pb['data'][0]                           # get the particle number information
    data_selected = data[(xx>xmin) & (xx<xmax),:]  # select particle number according to position
                                                   # for our case now, this doesn't make much difference.
    
    data_ekin = np.sum(data_selected,axis=0)       # dN, ?? can't remember... you might want to check what it does
    dE = ekin[1]-ekin[0]                           # dE, energy range
    total_weight = np.sum(data)                    # N, total number of the selected portion
    num = data_ekin * ekin / total_weight / dE     # E \frac{dN}{dE} \frac{1}{N} -- the y-axis
    
    return ekin, num, simu_time

# Function for 2D streak map

def prepare_streak_2D(case, num, field_name, frame):
    
    """
    case: string, Smilei case
    num: '0', instant; '1', averaged 
    field_name: string, name of the field
    frame: float, velocity of the reference frame
    """
    var = case.Field(num,field_name,units=["mm","ns","cm^-3","T","V/m"]) # find the data
    data_var = var.getData()                           # get the data out
    data_var_2D = np.vstack(data_var)                  # transform it into 2D with (t,x)
    data_var_t = var.getTimes()                        # get the t-axis
    data_var_x = var.getAxis('x')                      # get the x-axis
    
    data_var_x_2D, data_var_t_2D = np.meshgrid(data_var_x, data_var_t, indexing='xy') # make the interpolation
    
    data_var_x_2D_frame = data_var_x_2D - frame * data_var_t_2D - Lx/2.       # change the reference frame (and the label) 
                                                                                      # note the unit used
    return data_var_x_2D, data_var_x_2D_frame, data_var_t_2D, data_var_2D

def Particle_trajectory(case, species, mass, condition):
    
    """
    case: string, Smilei case
    species: string, name of the traced particle
    mass: float, mass of the traced particle, used when calcuating momentum/energy etc.
    condition: string, Smilei formatted, to select particles satisfying a certain conditions.
    frame: float, velocity of the reference frame
    """
    
#     me = 9.1e-31
#     c  = 3.0e8
#     wr = S.namelist.w_r
#     de = c / wr 
    
    tp = case.TrackParticles(species,
                             select = condition,
                             axes=['x','px','py','pz','Ex','Ey','Bz','w'],
                             units=[
                                 # 'mm',
                                 'ns'
                             ],                     # TODO: Use normalized unit during calculation
                             sort=True,
                            )
    data = tp.getData()                                           # get data
    time_tmp = data['times']                                      # get time, in unit of wpe^{-1}
    time_ns = np.linspace(0,tp.getTimes()[-1],time_tmp.size)      # transform time array into unit of ns.
    
    tp_px = data['px']                                            # extract all kinds of data
    tp_py = data['py']
    tp_pz = data['pz']
    tp_Ex = data['Ex']
    tp_Ey = data['Ey']
    tp_Bz = data['Bz']
    tp_x  = data['x']
    tp_weight = data['w']
    
#     tp_x_frame = tp_x * de * 1e3 - frame * time_ns              # change reference frame, do it later.
    
    tp_E  = (tp_px**2 + tp_py**2 + tp_pz**2)*(me*c)**2 / 2. / mass / qe / 1e6  # energy, in Unit of MeV
    tp_E = np.where(np.isfinite(tp_E),tp_E,0.)                                 # replace the inf/nan with 0.
    
    # find the particle with the highest energy at the last timestep 
    # (end of the simulation)
    [timestep, particle_number] = np.unravel_index(tp_E[-1].argmax(), tp_E.shape)
    
    tp_x_sub = tp_x[:,particle_number]
    tp_E_sub = tp_E[:,particle_number]
    
    return tp_x, tp_E, tp_px, tp_py, tp_pz, time_ns, tp_x_sub, tp_E_sub, tp_Ex, tp_Ey, tp_Bz, tp_weight, timestep, particle_number

## Calculate the kinetic energy gained by Ex, Ey, and the total.

def cal_kinetic_ene(part_id, E, Ex, Ey, px, py, time_ns):
    '''
    calculate the kinetic energy gained by Ex, Ey, and the total.
    '''
#     P_Ex = qe*ion2t_Ex[:, part_id]*kE*ion2t_px[:,part_id]*kp/mp
#     P_Ey = qe*ion2t_Ey[:, part_id]*kE*ion2t_py[:,part_id]*kp/mp
    
    P_Ex = qe*Ex[:, part_id]*kE*px[:,part_id]*me*c/mp
    P_Ey = qe*Ey[:, part_id]*kE*py[:,part_id]*me*c/mp

    dt = time_ns[2] - time_ns[1]
    
    t_P_tot5 = []
    for i in range(len(time_ns)-1):
        t_P_tot5.append((time_ns[i+1]+time_ns[i])/2.)

    K_Ex_5 = []
    for i in range(len(Ex[:, part_id])-1):
        K_Ex_5.append(sum(dt*1e-9*np.array(P_Ex[0:i+1]))/conv_MeV_J*1e3)

    K_Ey_5 = []
    for i in range(len(Ex[:, part_id])-1):
        K_Ey_5.append(sum(dt*1e-9*np.array(P_Ey[0:i+1]))/conv_MeV_J*1e3)


    # average functions every 10 timesteps
    def average(func):
        av = []
        for i in np.arange(0, len(func)-1,10):
            av.append((func[i]+func[i+1]+func[i+2]+func[i+3]+func[i+4]+func[i+5]+func[i+6]+func[i+7]+func[i+8]+func[i+9])/10)
        return av
    
    def average_3(func):
        av_3 = []
        for i in np.arange(0, len(func)-1,3):
            av_3.append((func[i]+func[i+1]+func[i+2])/3)
        return av_3

    # K_tot = np.array(average_3(E[:, part_id]*1e3))
    # K_tot_t = np.array(average_3(t_P_tot5))
    
    return t_P_tot5, K_Ex_5, K_Ey_5#, K_tot, K_tot_t
    

def plot_kinetic_ene(part_id, savedir, xmin0, xmax0, ymin0, ymax0, specie0):
    width = 3.2 * 2
    height = width / 1.618 
    fig, ax = plt.subplots()

    # ax.plot(K_tot_t,K_tot,color='green', label=r'$K_{tot}$', linewidth=2.0)
    ax.plot(t_P_tot5,K_Ex_5,color='red', linestyle='--',label=r'$K_{Ex}$',linewidth=2.0)
    ax.plot(t_P_tot5,K_Ey_5,color='blue',linestyle=':', label=r'$K_{Ey}$',linewidth=2.0)
    # ax.plot(t_P_tot5,np.array(K_Ex_5)+np.array(K_Ey_5)+K_tot[0],color='cyan', linestyle='-.', linewidth=1.0, label=r'$K_{Ex}+K_{Ey}+K_{tot0}$',)


    ax.set_xlabel('time (ns)')
    ax.set_xlim([xmin0,xmax0])
    ax.set_ylabel('$K_{tot}$ (keV)')
    ax.set_ylim([ymin0,ymax0])

    ax.legend()
    ax.grid(linestyle='--', alpha=0.5)
    ax.set_title('In '+ specie0 +' ID = {:.0f}'.format(part_id))

    fig.set_size_inches(width, height)
    fig.savefig(savedir+'KE_'+specie0+'_ID_'+str(part_id)+'.pdf', bbox_inches='tight',dpi=600)
    plt.close()

# conversion constants for fields and momentum (when taken from TrackParticle)
kE = me*c*wr/qe  # V/m
kp = me*c        # kg m/s
kB = me*wr/qe    # T
conv_MeV_J = 10**6*qe

In [7]:
def plot_kinetic_ene2(part_id, savedir, xmin0, xmax0, specie0):
    width = 3.2 * 2
    height = width / 1.618 
    fig, ax = plt.subplots()

    # ax.plot(K_tot_t,K_tot,color='green', label=r'$K_{tot}$', linewidth=2.0)
    ax.plot(t_P_tot5,K_Ex_5,color='red', linestyle='--',label=r'$K_{Ex}$',linewidth=2.0)
    ax.plot(t_P_tot5,K_Ey_5,color='blue',linestyle=':', label=r'$K_{Ey}$',linewidth=2.0)
    # ax.plot(t_P_tot5,np.array(K_Ex_5)+np.array(K_Ey_5)+K_tot[0],color='cyan', linestyle='-.', linewidth=1.0, label=r'$K_{Ex}+K_{Ey}+K_{tot0}$',)


    ax.set_xlabel('time (ns)')
    ax.set_xlim([xmin0,xmax0])
    ax.set_ylabel('$K_{tot}$ (keV)')
    # ax.set_ylim([ymin0,ymax0])

    ax.legend()
    ax.grid(linestyle='--', alpha=0.5)
    ax.set_title('In '+ specie0 +' ID = {:.0f}'.format(part_id))

    fig.set_size_inches(width, height)
    fig.savefig(savedir+'KE_'+specie0+'_ID_'+str(part_id)+'.pdf', bbox_inches='tight',dpi=600)
    plt.close()

In [8]:
def Particle_data_extract(case, species, mass):
    
    """
    case: string, Smilei case
    species: string, name of the traced particle
    mass: float, mass of the traced particle, used when calcuating momentum/energy etc.
    condition: string, Smilei formatted, to select particles satisfying a certain conditions.
    frame: float, velocity of the reference frame
    """
    
#     me = 9.1e-31
#     c  = 3.0e8
#     wr = S.namelist.w_r
#     de = c / wr 
    
    tp = case.TrackParticles(species,
                            #  select = condition,
                             axes=['x','px','py','pz','Ex','Ey','Bz','w'],
                             units=[
                                 'mm',
                                 'ns'
                             ],                     # TODO: Use normalized unit during calculation
                             sort=True,
                            )
    data = tp.getData()                                           # get data
    time_tmp = data['times']                                      # get time, in unit of wpe^{-1}
    time_ns = np.linspace(0,tp.getTimes()[-1],time_tmp.size)      # transform time array into unit of ns.
    
    tp_px = data['px']                                            # extract all kinds of data
    tp_py = data['py']
    tp_pz = data['pz']
    tp_Ex = data['Ex']
    tp_Ey = data['Ey']
    tp_Bz = data['Bz']
    tp_x  = data['x']
    tp_weight = data['w']
    
#     tp_x_frame = tp_x * de * 1e3 - frame * time_ns              # change reference frame, do it later.
    
    tp_E  = (tp_px**2 + tp_py**2 + tp_pz**2)*(me*c)**2 / 2. / mass / qe / 1e6  # energy, in Unit of MeV
    tp_E = np.where(np.isfinite(tp_E),tp_E,0.)                                 # replace the inf/nan with 0.
    
    # find the particle with the highest energy at the last timestep 
    # (end of the simulation)
    # [timestep, particle_number] = np.unravel_index(tp_E[-1].argmax(), tp_E.shape)
    
    # tp_x_sub = tp_x[:,particle_number]
    # tp_E_sub = tp_E[:,particle_number]
    
    return tp_x, tp_E

In [9]:
def spect_load_1d_iter(wkdir,iteration,species,xmin,xmax):
    """
    Inputs ----
    wkdir      : string, data directory
    iteration  : int,    number of timesteps used 
    species    : int,    which species you want to plot
                         according to your own diagnostic in the Namelist
    xmin, xmax : float,  spatial selections, NOTE: in unit of de
    
    Outputs ---
    ekin       : float,  x-axis, energy(E) in MeV
    num        : float,  y-axis, E \frac{dN}{dE} \frac{1}{N}
                                 N  is the total number of particles
                                 dN is the number of particles in each energy range (dE)
                                 dE is the energy range
    simu_time  : float,  simulation time
    """
    S = happi.Open(wkdir)                        # No need to open the data again.
    dt = S.namelist.d_t                            # get simulation timestep
    ts = S.ParticleBinning(species).getTimesteps() # get all the timesteps available for this diag.
    # iteration = int(ts[-2] * time)                 # choose the time you want by a factor of [0,1]*T_end
    simu_time = iteration * dt / wr                # convert it into real unit
    pb = S.ParticleBinning(species).get(iteration) # get the diag. data from the chosen timestep
    
    xx   = pb['x'] * de * 1e3                      # get position information and convert the unit to mm
    ekin = pb['ekin'] * 0.511                      # get energy information (E) and convert the unit to MeV -- the x-axis
    data = pb['data'][0]                           # get the particle number information
    data_selected = data[(xx>xmin) & (xx<xmax),:]  # select particle number according to position
                                                   # for our case now, this doesn't make much difference.
    
    data_ekin = np.sum(data_selected,axis=0)       # dN, ?? can't remember... you might want to check what it does
    dE = ekin[1]-ekin[0]                           # dE, energy range
    total_weight = np.sum(data)                    # N, total number of the selected portion
    num = data_ekin * ekin / total_weight / dE     # E \frac{dN}{dE} \frac{1}{N} -- the y-axis
    
    return ekin, num, simu_time

In [10]:
# ekin0, num0, t_end0 = spect_load_1d(wkdir[0], 0.75, 2, 0.0, Lx)
# ekin1, num1, t_end1 = spect_load_1d(wkdir[1], 1.0, 2, 0.0, Lx)
# ekin2, num2, t_end2 = spect_load_1d(wkdir, 0.2, 1, 0.0, Lx)

In [17]:
ekin2, num2, t_end2 = spect_load_1d_iter(wkdir[2], 1333280, 2, 0.0, Lx) # use .getTimesteps to find the proper time step.
ekin1, num1, t_end1 = spect_load_1d_iter(wkdir[1], 1333280, 2, 0.0, Lx)
ekin0, num0, t_end0 = spect_load_1d_iter(wkdir[0], 1333280, 2, 0.0, Lx)

Loaded simulation '/Users/yao/Desktop/Data/SS_2v_0_r0/'
Scanning for Scalar diagnostics
Scanning for Field diagnostics
Scanning for Probe diagnostics
Scanning for ParticleBinning diagnostics
Scanning for RadiationSpectrum diagnostics
Scanning for Performance diagnostics
Scanning for Screen diagnostics
Scanning for Tracked particle diagnostics
Scanning for new particle diagnostics
Loaded simulation '/Users/yao/Documents/Data/DS_9_r0/'
Loaded simulation '/Users/yao/Documents/Data/DS_9_r1/'
Scanning for Scalar diagnostics
Scanning for Field diagnostics
Scanning for Probe diagnostics
Scanning for ParticleBinning diagnostics
Scanning for RadiationSpectrum diagnostics
Scanning for Performance diagnostics
Scanning for Screen diagnostics
Scanning for Tracked particle diagnostics
Scanning for new particle diagnostics
Loaded simulation '/Users/yao/Documents/Data/SS_9_r0/'
Loaded simulation '/Users/yao/Documents/Data/SS_9_r1/'
Scanning for Scalar diagnostics
Scanning for Field diagnostics
Scannin

In [12]:
# x-t diagram from happi.streak

Bz0 = S0.Field(0,'Bz',units=['T','mm','ns'],
         cmap=newcmap,
        #  xmin=12,xmax=20,
        label='SSv1'
         )

Bz1 = S1.Field(0,'Bz',units=['T','mm','ns'],
         cmap=newcmap,
        #  xmin=12,xmax=20,
        label='DSv1',
        linestyle=':'
         )

Bz2 = S2.Field(0,'Bz',units=['T','mm','ns'],
         cmap=newcmap,
        #  xmin=12,xmax=20,
        label='SSv2',
        linestyle='--'
         )

happi.multiSlide(Bz0, Bz1, Bz2)


In [11]:
ssv1 = S0.ParticleBinning(2,
                   units=['MeV','ns'],
                   data_log=True,
                   color='blue',
                   linestyle='--',
                   sum={'x':'all'}).slide()

# dsv1 = S1.ParticleBinning(2,
#                    units=['keV','ns'],
#                    data_log=True,
#                    color='red',
#                    linestyle='-',
#                    sum={'x':'all'})#.slide()

# ssv2 = S2.ParticleBinning(2,
#                    units=['keV','ns'],
#                    data_log=True,
#                    color='black',
#                    linestyle=':',
#                    sum={'x':'all'})#.slide()

# happi.multiSlide(ssv1, dsv1, ssv2)


#2 - Number density of species # 0,3,6
    x from 0 to 2048 in 500 steps 
    ekin from 0 to 30 in 500 steps 

average for all x
The value in each bin is the sum of the `deposited_quantity` divided by the bin size



In [20]:
S0.ParticleBinning(2).getTimesteps()

array([      0,   16666,   33332,   49998,   66664,   83330,   99996,
        116662,  133328,  149994,  166660,  183326,  199992,  216658,
        233324,  249990,  266656,  283322,  299988,  316654,  333320,
        349986,  366652,  383318,  399984,  416650,  433316,  449982,
        466648,  483314,  499980,  516646,  533312,  549978,  566644,
        583310,  599976,  616642,  633308,  649974,  666640,  683306,
        699972,  716638,  733304,  749970,  766636,  783302,  799968,
        816634,  833300,  849966,  866632,  883298,  899964,  916630,
        933296,  949962,  966628,  983294,  999960, 1016626, 1033292,
       1049958, 1066624, 1083290, 1099956, 1116622, 1133288, 1149954,
       1166620, 1183286, 1199952, 1216618, 1233284, 1249950, 1266616,
       1283282, 1299948, 1316614, 1333280])

In [18]:
S0.ParticleBinning(3,
                   units=['keV','ns'],
                   data_log=True,
                   sum={'x':'all'}).slide()


#3 - Number density of species # 2,5,8
    x from 0 to 6144 in 500 steps 
    ekin from 0 to 0.1 in 500 steps 

average for all x
The value in each bin is the sum of the `deposited_quantity` divided by the bin size



/Users/yao/Smilei/happi/_Diagnostics/Diagnostic.py:857: RuntimeWarning: divide by zero encountered in log10
  return self._np.log10( self._dataLinAtTime(t) )


In [26]:
width  = 3.2 * 2
height = width / 1.618
fig, ax = plt.subplots()
fig.subplots_adjust(left=.2, bottom=.2, right=.9, top=.9)
num_max = max(num0.max(),num1.max(),num2.max())
# ax.loglog(ekin2, num2, '-g', label='{:.1f} ns'.format(t_end2*1e9), lw=2.0)
ax.semilogy(ekin0*1e3, num0/num_max, '-b', label='Single shock at {:.1f} ns'.format(t_end0*1e9), lw=2.0)
ax.semilogy(ekin1*1e3, num1/num_max, '-r',  label='Double shock at {:.1f} ns'.format(t_end1*1e9), lw=2.0)
ax.semilogy(ekin2*1e3, num2/num_max, '-k', label='Single shock vx2 at {:.1f} ns'.format(t_end2*1e9), lw=2.0)
ax.tick_params(axis='both',which='both', direction='in')
ax.set_xlabel(r'$E_{p}$ (keV)')
ax.set_ylabel(r'$A. U.$')
ax.set_xlim([0.0, 500])
# ax.set_xticks([0.01, 0.05, 0.10])
# ax.set_xticklabels([0.01, 0.05, 0.10])
ax.set_ylim([1e-6, 1])
ax.legend(loc='best', numpoints=1, fancybox=True, fontsize=12)
ax.grid(which='major',linestyle='--',alpha=0.5)
fig.set_size_inches(width, height)

In [27]:
fig.savefig('/Users/yao/Desktop/energy_spectrum_compare.png',transparent=True,dpi=300)

In [ ]:
fig.savefig('/Users/yao/Desktop/test.pdf',transparent=True,dpi=300)

In [84]:
# Fig.3, particle trajectories illustrating the acceleration mechanism

# prepare packages

import numpy as np
import matplotlib.pyplot as plt
import matplotlib as mpl

from matplotlib.collections import LineCollection
from matplotlib.colors import ListedColormap, BoundaryNorm, LogNorm

from mpl_toolkits.axes_grid1 import make_axes_locatable
from matplotlib.ticker import LogLocator

# prepare to convert to center-of-mass reference frame 
n1   = 2e18     # drifting plasma, number density
n2   = 1e18     # ambient plasma, number density
v1   = 3.0e6    # drifting velocity, m/s
v1_SS2   = 6.0e6    # drifting velocity, m/s
v2   = 0.0
vcom = (n1*v1 + n2*v2) / (n1+n2) # center-of-mass reference frame, m/s
vcom_SS2 = (n1*v1_SS2 + n2*v2) / (n1+n2) # center-of-mass reference frame, m/s
vcom_mm_ns = vcom * 1e-6         # in unit of mm/ns
vcom_SS2_mm_ns = vcom_SS2 * 1e-6         # in unit of mm/ns

# prepare to convert to discontinuity reference frame
vcd_SS1 = 1.93  # measured from the x-t diagram
vcd_SS2 = 1.93*2
vcd =0 # 0.86*2+0.25 # mm/ns, read from the x-t plot.

# get data for 2D streak map
# Bz_x_0, Bz_x, Bz_t, Bz = prepare_streak_2D(S, 0, 'Bz', vcom_mm_ns)
# ni_x_0, ni_x, ni_t, ni = prepare_streak_2D(S, 0, 'Rho_ion1+Rho_ion2', vcom_mm_ns)

Bz0_x_1, Bz0_x_cd,  Bz0_t_cd,  Bz0_cd  = prepare_streak_2D(S0, 0, 'Bz', vcd_SS1)
ni0_x_1, ni0_x_cd,  ni0_t_cd,  ni0_cd  = prepare_streak_2D(S0, 0, 'Rho_ion1+Rho_ion2+Rho_ion3', vcd_SS1)
Ex0_x_2, Ex0_x_cd2, Ex0_t_cd2, Ex0_cd2 = prepare_streak_2D(S0, 1, 'Ex', vcd_SS1)
Ey0_x_2, Ey0_x_cd2, Ey0_t_cd2, Ey0_cd2 = prepare_streak_2D(S0, 1, 'Ey', vcd_SS1)
Bz0_x_2, Bz0_x_cd2, Bz0_t_cd2, Bz0_cd2 = prepare_streak_2D(S0, 1, 'Bz', vcd_SS1)

Bz1_x_1, Bz1_x_cd,  Bz1_t_cd,  Bz1_cd  = prepare_streak_2D(S1, 0, 'Bz', vcd)
ni1_x_1, ni1_x_cd,  ni1_t_cd,  ni1_cd  = prepare_streak_2D(S1, 0, 'Rho_ion1+Rho_ion2+Rho_ion3', vcd)
Ex1_x_2, Ex1_x_cd2, Ex1_t_cd2, Ex1_cd2 = prepare_streak_2D(S1, 1, 'Ex', vcd)
Ey1_x_2, Ey1_x_cd2, Ey1_t_cd2, Ey1_cd2 = prepare_streak_2D(S1, 1, 'Ey', vcd)
Bz1_x_2, Bz1_x_cd2, Bz1_t_cd2, Bz1_cd2 = prepare_streak_2D(S1, 1, 'Bz', vcd)

Bz2_x_1, Bz2_x_cd,  Bz2_t_cd,  Bz2_cd  = prepare_streak_2D(S2, 0, 'Bz', vcd_SS2)
ni2_x_1, ni2_x_cd,  ni2_t_cd,  ni2_cd  = prepare_streak_2D(S2, 0, 'Rho_ion1+Rho_ion2+Rho_ion3', vcd_SS2)
Ex2_x_2, Ex2_x_cd2, Ex2_t_cd2, Ex2_cd2 = prepare_streak_2D(S2, 1, 'Ex', vcd_SS2)
Ey2_x_2, Ey2_x_cd2, Ey2_t_cd2, Ey2_cd2 = prepare_streak_2D(S2, 1, 'Ey', vcd_SS2)
Bz2_x_2, Bz2_x_cd2, Bz2_t_cd2, Bz2_cd2 = prepare_streak_2D(S2, 1, 'Bz', vcd_SS2)

In [29]:
# particle selection condition
# TODO: in this Smilei formatted string, you can't use the self-defined constants.
condition_p1 = "any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.16))"
condition_p2 = "any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.2))"
condition_p3 = "any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.125))"

# get particle tracer data

ion1t_x, ion1t_E, \
ion1t_px, ion1t_py, ion1t_pz, \
ion1t_time_ns, ion1t_x_sub, ion1t_E_sub, \
ion1t_Ex, ion1t_Ey, ion1t_Bz, \
ion1t_weight, ion1t_ts, ion1t_id = Particle_trajectory(S0, 'ion1t', mp, condition_p1)

ion2t_x, ion2t_E, \
ion2t_px, ion2t_py, ion2t_pz, \
ion2t_time_ns, ion2t_x_sub, ion2t_E_sub, \
ion2t_Ex, ion2t_Ey, ion2t_Bz, \
ion2t_weight, ion2t_ts, ion2t_id = Particle_trajectory(S0, 'ion2t', mp, condition_p2)

ion3t_x, ion3t_E, \
ion3t_px, ion3t_py, ion3t_pz, \
ion3t_time_ns, ion3t_x_sub, ion3t_E_sub, \
ion3t_Ex, ion3t_Ey, ion3t_Bz, \
ion3t_weight, ion3t_ts, ion3t_id = Particle_trajectory(S0, 'ion3t', mp, condition_p3)

# SS_9:
# with p1 = 0.16,  ion1t has 4 particles
# with p2 = 0.2,   ion2t has 3 particles
# with p3 = 0.125, ion3t has 2 particles



Selecting particles ... (this may take a while)
   Selecting block `any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.16))`, at time 400     (100.00% of particles)
   Selecting block `any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.16))`, at time 800     (100.00% of particles)
   Selecting block `any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.16))`, at time 1200     (100.00% of particles)
   Selecting block `any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.16))`, at time 1600     (100.00% of particles)
   Selecting block `any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.16))`, at time 2000     (100.00% of particles)
   Selecting block `any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.16))`, at time 2400     (100.00% of particles)
   Selecting block `any(t>0, ((px**2+py**2+pz**2)*(9.1

In [24]:
## extract the particle information for ML

ion1t_x, ion1t_E  = Particle_data_extract(S1, 'ion1t', mp)
ion2t_x, ion2t_E  = Particle_data_extract(S1, 'ion2t', mp)
ion3t_x, ion3t_E  = Particle_data_extract(S1, 'ion3t', mp)


Removing dead particles ...
Kept 12800 particles
Loading data ...
   axis: x
   axis: px
   axis: py
   axis: pz
   axis: Ex
   axis: Ey
   axis: Bz
   axis: w
Process broken lines ...
... done
Removing dead particles ...
Kept 5120 particles
Loading data ...
   axis: x
   axis: px
   axis: py
   axis: pz
   axis: Ex
   axis: Ey
   axis: Bz
   axis: w
Process broken lines ...
... done
Removing dead particles ...
Kept 12800 particles
Loading data ...
   axis: x
   axis: px
   axis: py
   axis: pz
   axis: Ex
   axis: Ey
   axis: Bz
   axis: w
Process broken lines ...
... done


In [26]:
np.savetxt("/Users/yao/Desktop/ion1t_E.txt", ion1t_E)

In [27]:
np.save("/Users/yao/Desktop/ion1t_E.txt", ion1t_E,allow_pickle=False)

In [28]:
np.savez_compressed("/Users/yao/Desktop/1DPIC_shock_collide", ion1_x=ion1t_x, ion1_E=ion1t_E, ion2_x=ion2t_x, ion2_E=ion2t_E, ion3_x=ion3t_x, ion3_E=ion3t_E)

In [30]:
ion2t_E.shape

(5671, 5120)

In [30]:
# particle selection condition
# TODO: in this Smilei formatted string, you can't use the self-defined constants.
condition_p1 = "any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.46))"
condition_p2 = "any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.18))"
condition_p3 = "any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.46))"

# get particle tracer data

ion1t_x_DS, ion1t_E_DS, \
ion1t_px_DS, ion1t_py_DS, ion1t_pz_DS, \
ion1t_time_ns_DS, ion1t_x_sub_DS, ion1t_E_sub_DS, \
ion1t_Ex_DS, ion1t_Ey_DS, ion1t_Bz_DS, \
ion1t_weight_DS, ion1t_ts_DS, ion1t_id_DS = Particle_trajectory(S1, 'ion1t', mp, condition_p1)

ion2t_x_DS, ion2t_E_DS, \
ion2t_px_DS, ion2t_py_DS, ion2t_pz_DS, \
ion2t_time_ns_DS, ion2t_x_sub_DS, ion2t_E_sub_DS, \
ion2t_Ex_DS, ion2t_Ey_DS, ion2t_Bz_DS, \
ion2t_weight_DS, ion2t_ts_DS, ion2t_id_DS = Particle_trajectory(S1, 'ion2t', mp, condition_p2)

ion3t_x_DS, ion3t_E_DS, \
ion3t_px_DS, ion3t_py_DS, ion3t_pz_DS, \
ion3t_time_ns_DS, ion3t_x_sub_DS, ion3t_E_sub_DS, \
ion3t_Ex_DS, ion3t_Ey_DS, ion3t_Bz_DS, \
ion3t_weight_DS, ion3t_ts_DS, ion3t_id_DS = Particle_trajectory(S1, 'ion3t', mp, condition_p3)

# DS_9:
# with p1 = 0.46, ion1t has 4 particles
# with p2 = 0.18, ion2t has 4 particles
# with p3 = 0.46, ion3t has 4 particles

Selecting particles ... (this may take a while)
   Selecting block `any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.46))`, at time 400     (100.00% of particles)
   Selecting block `any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.46))`, at time 800     (100.00% of particles)
   Selecting block `any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.46))`, at time 1200     (100.00% of particles)
   Selecting block `any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.46))`, at time 1600     (100.00% of particles)
   Selecting block `any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.46))`, at time 2000     (100.00% of particles)
   Selecting block `any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.46))`, at time 2400     (100.00% of particles)
   Selecting block `any(t>0, ((px**2+py**2+pz**2)*(9.1

In [ ]:
# particle selection condition
# TODO: in this Smilei formatted string, you can't use the self-defined constants.
condition_p1 = "any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.45))"
condition_p2 = "any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.6))"
condition_p3 = "any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.5))"

# get particle tracer data

ion1t_x_SS2, ion1t_E_SS2, \
ion1t_px_SS2, ion1t_py_SS2, ion1t_pz_SS2, \
ion1t_time_ns_SS2, ion1t_x_sub_SS2, ion1t_E_sub_SS2, \
ion1t_Ex_SS2, ion1t_Ey_SS2, ion1t_Bz_SS2, \
ion1t_weight_SS2, ion1t_ts_SS2, ion1t_id_SS2 = Particle_trajectory(S2, 'ion1t', mp, condition_p1)

ion2t_x_SS2, ion2t_E_SS2, \
ion2t_px_SS2, ion2t_py_SS2, ion2t_pz_SS2, \
ion2t_time_ns_SS2, ion2t_x_sub_SS2, ion2t_E_sub_SS2, \
ion2t_Ex_SS2, ion2t_Ey_SS2, ion2t_Bz_SS2, \
ion2t_weight_SS2, ion2t_ts_SS2, ion2t_id_SS2 = Particle_trajectory(S2, 'ion2t', mp, condition_p2)

ion3t_x_SS2, ion3t_E_SS2, \
ion3t_px_SS2, ion3t_py_SS2, ion3t_pz_SS2, \
ion3t_time_ns_SS2, ion3t_x_sub_SS2, ion3t_E_sub_SS2, \
ion3t_Ex_SS2, ion3t_Ey_SS2, ion3t_Bz_SS2, \
ion3t_weight_SS2, ion3t_ts_SS2, ion3t_id_SS2 = Particle_trajectory(S2, 'ion3t', mp, condition_p3)

# SS_2v_0_r0:
# with p1 = 0.45,  ion1t has 12 particles
# with p2 = 0.6,   ion2t has 12 particles
# with p3 = 0.5,   ion3t has 13 particles



Selecting particles ... (this may take a while)
   Selecting block `any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.45))`, at time 400     (100.00% of particles)
   Selecting block `any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.45))`, at time 800     (100.00% of particles)
   Selecting block `any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.45))`, at time 1200     (100.00% of particles)
   Selecting block `any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.45))`, at time 1600     (100.00% of particles)
   Selecting block `any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.45))`, at time 2000     (100.00% of particles)
   Selecting block `any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.45))`, at time 2400     (100.00% of particles)
   Selecting block `any(t>0, ((px**2+py**2+pz**2)*(9.1

In [ ]:
S.TrackParticles('eon2t',axes=['Id']).getData()

In [46]:
## check every particle

# SS_9:
# with p1 = 0.16,  ion1t has 4 particles
# with p2 = 0.2,   ion2t has 3 particles
# with p3 = 0.125, ion3t has 2 particles

xmin0 = 0
xmax0 = 4
ymin0 = -400
ymax0 = 700

for part_id in range(4):
    t_P_tot5, K_Ex_5, K_Ey_5 = cal_kinetic_ene(part_id, ion1t_E, ion1t_Ex, 
                                                               ion1t_Ey, ion1t_px, ion1t_py, 
                                                               ion1t_time_ns)
    plot_kinetic_ene(part_id, '/Users/yao/Desktop/SSv1/',xmin0, xmax0, ymin0, ymax0, 'ion1t')

for part_id in range(3):
    t_P_tot5, K_Ex_5, K_Ey_5 = cal_kinetic_ene(part_id, ion2t_E, ion2t_Ex, 
                                                               ion2t_Ey, ion2t_px, ion2t_py, 
                                                               ion2t_time_ns)
    plot_kinetic_ene(part_id, '/Users/yao/Desktop/SSv1/',xmin0, xmax0, ymin0, ymax0, 'ion2t')



for part_id in range(2):
    t_P_tot5, K_Ex_5, K_Ey_5 = cal_kinetic_ene(part_id, ion3t_E, ion3t_Ex, 
                                                               ion3t_Ey, ion3t_px, ion3t_py, 
                                                               ion3t_time_ns)
    plot_kinetic_ene(part_id, '/Users/yao/Desktop/SSv1/',xmin0, xmax0, ymin0, ymax0, 'ion3t')




In [45]:
## check every particle


# DS_9:
# with p1 = 0.46, ion1t has 4 particles
# with p2 = 0.18, ion2t has 4 particles
# with p3 = 0.46, ion3t has 4 particles

xmin0 = 0
xmax0 = 4
ymin0 = -400
ymax0 = 700

for part_id in range(4):
    t_P_tot5, K_Ex_5, K_Ey_5 = cal_kinetic_ene(part_id, ion1t_E_DS, ion1t_Ex_DS, 
                                                               ion1t_Ey_DS, ion1t_px_DS, ion1t_py_DS, 
                                                               ion1t_time_ns_DS)
    plot_kinetic_ene(part_id, '/Users/yao/Desktop/DSv1/',xmin0, xmax0, ymin0, ymax0, 'ion1t')

for part_id in range(4):
    t_P_tot5, K_Ex_5, K_Ey_5 = cal_kinetic_ene(part_id, ion2t_E_DS, ion2t_Ex_DS, 
                                                               ion2t_Ey_DS, ion2t_px_DS, ion2t_py_DS, 
                                                               ion2t_time_ns_DS)
    plot_kinetic_ene(part_id, '/Users/yao/Desktop/DSv1/',xmin0, xmax0, ymin0, ymax0, 'ion2t')



for part_id in range(4):
    t_P_tot5, K_Ex_5, K_Ey_5 = cal_kinetic_ene(part_id, ion3t_E_DS, ion3t_Ex_DS, 
                                                               ion3t_Ey_DS, ion3t_px_DS, ion3t_py_DS, 
                                                               ion3t_time_ns_DS)
    plot_kinetic_ene(part_id, '/Users/yao/Desktop/DSv1/',xmin0, xmax0, ymin0, ymax0, 'ion3t')



In [43]:
## check every particle


# SS_2v_0_r0:
# with p1 = 0.45,  ion1t has 12 particles
# with p2 = 0.6,   ion2t has 12 particles
# with p3 = 0.5,   ion3t has 13 particles

xmin0 = 0
xmax0 = 4
ymin0 = -400
ymax0 = 700 

for part_id in range(12):
    t_P_tot5, K_Ex_5, K_Ey_5 = cal_kinetic_ene(part_id, ion1t_E_SS2, ion1t_Ex_SS2, 
                                                               ion1t_Ey_SS2, ion1t_px_SS2, ion1t_py_SS2, 
                                                               ion1t_time_ns_SS2)
    plot_kinetic_ene(part_id, '/Users/yao/Desktop/SSv2/',xmin0, xmax0, 
                      ymin0, ymax0, 
                      'ion1t')

for part_id in range(12):
    t_P_tot5, K_Ex_5, K_Ey_5 = cal_kinetic_ene(part_id, ion2t_E_SS2, ion2t_Ex_SS2, 
                                                               ion2t_Ey_SS2, ion2t_px_SS2, ion2t_py_SS2, 
                                                               ion2t_time_ns_SS2)
    plot_kinetic_ene(part_id, '/Users/yao/Desktop/SSv2/',xmin0, xmax0, 
                      ymin0, ymax0, 
                      'ion2t')



for part_id in range(12):
    t_P_tot5, K_Ex_5, K_Ey_5 = cal_kinetic_ene(part_id, ion3t_E_SS2, ion3t_Ex_SS2, 
                                                               ion3t_Ey_SS2, ion3t_px_SS2, ion3t_py_SS2, 
                                                               ion3t_time_ns_SS2)
    plot_kinetic_ene(part_id, '/Users/yao/Desktop/SSv2/',xmin0, xmax0, 
                      ymin0, ymax0, 
                      'ion3t')



In [ ]:
for part_id in range(54):
    t_P_tot5, K_Ex_5, K_Ey_5, K_tot, K_tot_t = cal_kinetic_ene(part_id, ion1t_E, ion1t_Ex, 
                                                               ion1t_Ey, ion1t_px, ion1t_py, 
                                                               ion1t_time_ns)
    plot_kinetic_ene(part_id, wkdir[0])

In [86]:
nt = ion1t_time_ns.size
t_end = S0.namelist.t_end / wr * 1e9
time_ns = np.linspace(0.,t_end,nt)

ion3t_x_frame = np.zeros_like(ion3t_x)
ion3t_x_vcd   = np.zeros_like(ion3t_x)
# ion2t_px_vcd  = zeros_like(ion2t_px)
# ion2t_E_vcd  = zeros_like(ion2t_E)
for i in range(2):     # Note that here the loop-number should be the num. of particles.
    # ion2t_x_frame[:,i] = ion2t_x[:,i]*de*1e3 - vcom_mm_ns*time_ns - Lx/2.
    ion3t_x_vcd[:,i]   = ion3t_x[:,i]*de*1e3 - vcd_SS1       *ion3t_time_ns - Lx/2.
#     ion2t_px_vcd[:,i]  = ion2t_px[:,i]*me*c - vcd*1e6*mp   # in the unit of kgm/s
#     ion2t_E_vcd[:,i]   = (ion2t_px_vcd[:,i]**2 + (ion2t_py[:,i]*me*c)**2 + (ion2t_pz[:,i]*me*c)**2) / 2. / mp / qe / 1e6

ion2t_x_frame = np.zeros_like(ion2t_x)
ion2t_x_vcd   = np.zeros_like(ion2t_x)
# ion2t_px_vcd  = zeros_like(ion2t_px)
# ion2t_E_vcd  = zeros_like(ion2t_E)
for i in range(3):     # Note that here the loop-number should be the num. of particles.
    # ion2t_x_frame[:,i] = ion2t_x[:,i]*de*1e3 - vcom_mm_ns*time_ns - Lx/2.
    ion2t_x_vcd[:,i]   = ion2t_x[:,i]*de*1e3 - vcd_SS1       *ion2t_time_ns - Lx/2.
#     ion2t_px_vcd[:,i]  = ion2t_px[:,i]*me*c - vcd*1e6*mp   # in the unit of kgm/s
#     ion2t_E_vcd[:,i]   = (ion2t_px_vcd[:,i]**2 + (ion2t_py[:,i]*me*c)**2 + (ion2t_pz[:,i]*me*c)**2) / 2. / mp / qe / 1e6
    
ion1t_x_frame = np.zeros_like(ion1t_x)
ion1t_x_vcd   = np.zeros_like(ion1t_x)
ion1t_px_vcd  = np.zeros_like(ion1t_px)
ion1t_E_vcd   = np.zeros_like(ion1t_E)
for i in range(4):
    # ion1t_x_frame[:,i] = ion1t_x[:,i]*de*1e3 - vcom_mm_ns*time_ns - Lx/2.
    ion1t_x_vcd[:,i]   = ion1t_x[:,i]*de*1e3 - vcd_SS1       *ion1t_time_ns - Lx/2.
#     ion1t_px_vcd[:,i]  = ion1t_px[:,i]*me*c - vcd*1e6*mp   # in the unit of kgm/s
#     ion1t_E_vcd[:,i]   = (ion1t_px_vcd[:,i]**2 + (ion1t_py[:,i]*me*c)**2 + (ion1t_pz[:,i]*me*c)**2) / 2. / mp / qe / 1e6

In [48]:
vcd

0

In [96]:
for id in range(4):
    plt.plot(ion1t_x_vcd[:,id],  ion1t_time_ns, lw=2.0, label='ion1t: ID = {:.0f}'.format(id))

for id in range(3):
    plt.plot(ion2t_x_vcd[:,id],  ion1t_time_ns, lw=2.0, label='ion2t: ID = {:.0f}'.format(id), linestyle='--')

for id in range(2):
    plt.plot(ion3t_x_vcd[:,id],  ion1t_time_ns, lw=2.0, label='ion3t: ID = {:.0f}'.format(id), linestyle=':')

# plt.legend()
plt.ylim([0,2.5])
plt.xlim([-7,7])
plt.xlabel('x (mm)')
plt.ylabel('time (ns)')

Text(0, 0.5, 'time (ns)')

In [89]:
# nt = ion1t_time_ns_DS.size
# t_end = S1.namelist.t_end / wr * 1e9
# time_ns = np.linspace(0.,t_end,nt)

# ion2t_x_frame = np.zeros_like(ion2t_x_DS)
ion2t_x_vcd_DS   = np.zeros_like(ion2t_x_DS)
# ion2t_px_vcd  = zeros_like(ion2t_px)
# ion2t_E_vcd  = zeros_like(ion2t_E)
for i in range(4):     # Note that here the loop-number should be the num. of particles.
    # ion2t_x_frame[:,i] = ion2t_x[:,i]*de*1e3 - vcom_mm_ns*time_ns - Lx/2.
    ion2t_x_vcd_DS[:,i]   = ion2t_x_DS[:,i]*de*1e3 - vcd       *ion2t_time_ns_DS - Lx/2.
#     ion2t_px_vcd[:,i]  = ion2t_px[:,i]*me*c - vcd*1e6*mp   # in the unit of kgm/s
#     ion2t_E_vcd[:,i]   = (ion2t_px_vcd[:,i]**2 + (ion2t_py[:,i]*me*c)**2 + (ion2t_pz[:,i]*me*c)**2) / 2. / mp / qe / 1e6
    
# ion1t_x_frame = np.zeros_like(ion1t_x)
ion1t_x_vcd_DS   = np.zeros_like(ion1t_x_DS)
# ion1t_px_vcd  = np.zeros_like(ion1t_px)
# ion1t_E_vcd   = np.zeros_like(ion1t_E)
for i in range(4):
    # ion1t_x_frame[:,i] = ion1t_x[:,i]*de*1e3 - vcom_mm_ns*time_ns - Lx/2.
    ion1t_x_vcd_DS[:,i]   = ion1t_x_DS[:,i]*de*1e3 - vcd       *ion1t_time_ns_DS - Lx/2.
#     ion1t_px_vcd[:,i]  = ion1t_px[:,i]*me*c - vcd*1e6*mp   # in the unit of kgm/s
#     ion1t_E_vcd[:,i]   = (ion1t_px_vcd[:,i]**2 + (ion1t_py[:,i]*me*c)**2 + (ion1t_pz[:,i]*me*c)**2) / 2. / mp / qe / 1e6


# ion1t_x_frame = np.zeros_like(ion1t_x)
ion3t_x_vcd_DS   = np.zeros_like(ion3t_x_DS)
# ion1t_px_vcd  = np.zeros_like(ion1t_px)
# ion1t_E_vcd   = np.zeros_like(ion1t_E)
for i in range(4):
    # ion1t_x_frame[:,i] = ion1t_x[:,i]*de*1e3 - vcom_mm_ns*time_ns - Lx/2.
    ion3t_x_vcd_DS[:,i]   = ion3t_x_DS[:,i]*de*1e3 - vcd       *ion3t_time_ns_DS - Lx/2.
#     ion1t_px_vcd[:,i]  = ion1t_px[:,i]*me*c - vcd*1e6*mp   # in the unit of kgm/s
#     ion1t_E_vcd[:,i]   = (ion1t_px_vcd[:,i]**2 + (ion1t_py[:,i]*me*c)**2 + (ion1t_pz[:,i]*me*c)**2) / 2. / mp / qe / 1e6

In [97]:
for id in range(4):
    plt.plot(ion1t_x_vcd_DS[:,id],  ion1t_time_ns_DS, lw=2.0, label='ion1t: ID = {:.0f}'.format(id))

for id in range(4):
    plt.plot(ion2t_x_vcd_DS[:,id],  ion2t_time_ns_DS, lw=2.0, label='ion2t: ID = {:.0f}'.format(id), linestyle='--')

for id in range(4):
    plt.plot(ion3t_x_vcd_DS[:,id],  ion3t_time_ns_DS, lw=2.0, label='ion2t: ID = {:.0f}'.format(id), linestyle=':')

plt.ylim([0,2.5])
plt.xlim([-7,7])
plt.xlabel('x (mm)')
plt.ylabel('time (ns)')
# plt.legend()

Text(0, 0.5, 'time (ns)')

In [92]:
# for the case of SSv2:

ion2t_x_vcd_SS2   = np.zeros_like(ion2t_x_SS2)

for i in range(12):     # Note that here the loop-number should be the num. of particles.
    ion2t_x_vcd_SS2[:,i]   = ion2t_x_SS2[:,i]*de*1e3 - vcd_SS2       *ion2t_time_ns_SS2 - Lx/2.

ion1t_x_vcd_SS2   = np.zeros_like(ion1t_x_SS2)
for i in range(12):
    ion1t_x_vcd_SS2[:,i]   = ion1t_x_SS2[:,i]*de*1e3 - vcd_SS2       *ion1t_time_ns_SS2 - Lx/2.

ion3t_x_vcd_SS2   = np.zeros_like(ion3t_x_SS2)
for i in range(13):
    ion3t_x_vcd_SS2[:,i]   = ion3t_x_SS2[:,i]*de*1e3 - vcd_SS2       *ion3t_time_ns_SS2 - Lx/2.


In [94]:
for id in range(12):
    plt.plot(ion1t_x_vcd_SS2[:,id],  ion1t_time_ns_SS2, lw=2.0, label='ion1t: ID = {:.0f}'.format(id))

for id in range(12):
    plt.plot(ion2t_x_vcd_SS2[:,id],  ion2t_time_ns_SS2, lw=2.0, label='ion2t: ID = {:.0f}'.format(id), linestyle='--')

for id in range(13):
    plt.plot(ion3t_x_vcd_SS2[:,id],  ion3t_time_ns_SS2, lw=2.0, label='ion2t: ID = {:.0f}'.format(id), linestyle=':')

plt.ylim([0,2.5])
plt.xlim([-7,7])
plt.xlabel('x (mm)')
plt.ylabel('time (ns)')
# plt.legend()

Text(0, 0.5, 'time (ns)')

In [71]:
# From this point, the post-process will become quite customized.
# It will be highly dependent on what you want to show.

# Draw the figure of x-t-ni/Bz
width = 3.2 * 3
height = width / 1.618
fig, axs = plt.subplots()

# cs1 = axs.pcolormesh(Bz_x_cd2, Bz_t_cd2, np.log10(Bz_cd2**2),cmap=plt.cm.Greys)
# cs1 = axs.pcolormesh(Bz_x_cd2, Bz_t_cd2, Bz_cd2,cmap=newcmap,vmin=0,vmax=200)
cs1 = axs.pcolormesh(Ey0_x_cd2, Ey0_t_cd2, Ey0_cd2/1e8,cmap='seismic',
                     vmin=-1.5,vmax=1.5
                     )

# cs1 = axs.pcolormesh(ni_x, ni_t, ni,cmap=plt.cm.jet)#,vmin=0,vmax=6.0e18)
# cs1 = axs.pcolormesh(ni_x_cd, ni_t_cd, ni_cd,cmap=newcmap,
#                      vmin=0,vmax=25.0
#                      )
# cs1.cmap.set_under(color='white')
# cs1.cmap.set_over(color='black')
cs1.cmap.set_under(color='blue')
cs1.cmap.set_over(color='red')
ax1_divider = make_axes_locatable(axs)
cax1=ax1_divider.append_axes("right", size="4%", pad="1%")
# cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$log_{10}(|B_z|^2)$')
# cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$B_z$ (T)')
cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$E_y$ (1e8 V/m)')
# cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$n_i$ (1e18 cm$^{-3}$)')
cbar1.ax.tick_params()
cax1.xaxis.set_ticks_position("top")
axs.tick_params(axis='both')
axs.set_xlabel('x (mm)')
axs.set_ylabel('t (ns)')

# axs.plot(ion2t_x_vcd[:,0:46:4],  time_ns, lw=2.0, ls='--')
# axs.plot(ion1t_x_vcd[:,0:111:10],  time_ns, lw=2.0)

# # axs.plot(ion2t_x_frame[:,0],  time_ns, lw=2.0, color='blue',   ls='--')
# # axs.plot(ion2t_x_frame[:,7],  time_ns, lw=2.0, color='red',  ls='--')
# # axs.plot(ion2t_x_frame[:,14], time_ns, lw=2.0, color='green', ls='--')
# # axs.plot(ion1t_x_frame[:,0],  time_ns, lw=2.0, color='black')
# # axs.plot(ion1t_x_frame[:,2],  time_ns, lw=2.0, color='m')

# # axs.plot(ion2t_x_vcd[:,0],  time_ns, lw=2.0, color='blue',   ls='--')
# axs.plot(ion2t_x_vcd[:,7],  time_ns, lw=2.0, color='red',  ls='--')
# # axs.plot(ion2t_x_vcd[:,14], time_ns, lw=2.0, color='green', ls='--')
# axs.plot(ion1t_x_vcd[:,0],  time_ns, lw=2.0, color='black')
# axs.plot(ion1t_x_vcd[:,2],  time_ns, lw=2.0, color='m')


axs.set_xlim([-4,4])
axs.set_ylim([0,4])
axs.set_aspect(1)

fig.set_size_inches(width,height)
fig.tight_layout()



In [41]:
# fig.savefig('/Users/yao/Desktop/'+'trace_ni_xt2'+'.png',bbox_inches='tight',dpi=600)
# fig.savefig('/Users/yao/Desktop/'+'density_x_t'+'.png',bbox_inches='tight',dpi=600)
# fig.savefig('/Users/yao/Desktop/'+'Bz_x_t'+'.png',bbox_inches='tight',dpi=600)
fig.savefig('/Users/yao/Desktop/'+'Ey_x_t'+'.png',bbox_inches='tight',dpi=600)

In [72]:
# From this point, the post-process will become quite customized.
# It will be highly dependent on what you want to show.

# Draw the figure of x-t-ni/Bz
width = 3.2 * 3
height = width / 1.618
fig, axs = plt.subplots()

# cs1 = axs.pcolormesh(Bz_x_cd2, Bz_t_cd2, np.log10(Bz_cd2**2),cmap=plt.cm.Greys)
# cs1 = axs.pcolormesh(Bz_x_cd2, Bz_t_cd2, Bz_cd2,cmap=newcmap,vmin=0,vmax=200)
cs1 = axs.pcolormesh(Ey1_x_cd2, Ey1_t_cd2, Ey1_cd2/1e8,cmap='seismic',
                     vmin=-1.5,vmax=1.5
                     )

# cs1 = axs.pcolormesh(ni_x, ni_t, ni,cmap=plt.cm.jet)#,vmin=0,vmax=6.0e18)
# cs1 = axs.pcolormesh(ni_x_cd, ni_t_cd, ni_cd,cmap=newcmap,
#                      vmin=0,vmax=25.0
#                      )
# cs1.cmap.set_under(color='white')
# cs1.cmap.set_over(color='black')
cs1.cmap.set_under(color='blue')
cs1.cmap.set_over(color='red')
ax1_divider = make_axes_locatable(axs)
cax1=ax1_divider.append_axes("right", size="4%", pad="2%")
# cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$log_{10}(|B_z|^2)$')
# cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$B_z$ (T)')
cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$E_y$ (1e8 V/m)')
# cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$n_i$ (1e18 cm$^{-3}$)')
cbar1.ax.tick_params()
cax1.xaxis.set_ticks_position("top")
axs.tick_params(axis='both')
axs.set_xlabel('x (mm)')
axs.set_ylabel('t (ns)')

# axs.plot(ion2t_x_vcd[:,0:46:4],  time_ns, lw=2.0, ls='--')
# axs.plot(ion1t_x_vcd[:,0:111:10],  time_ns, lw=2.0)

# # axs.plot(ion2t_x_frame[:,0],  time_ns, lw=2.0, color='blue',   ls='--')
# # axs.plot(ion2t_x_frame[:,7],  time_ns, lw=2.0, color='red',  ls='--')
# # axs.plot(ion2t_x_frame[:,14], time_ns, lw=2.0, color='green', ls='--')
# # axs.plot(ion1t_x_frame[:,0],  time_ns, lw=2.0, color='black')
# # axs.plot(ion1t_x_frame[:,2],  time_ns, lw=2.0, color='m')

# # axs.plot(ion2t_x_vcd[:,0],  time_ns, lw=2.0, color='blue',   ls='--')
# axs.plot(ion2t_x_vcd[:,7],  time_ns, lw=2.0, color='red',  ls='--')
# # axs.plot(ion2t_x_vcd[:,14], time_ns, lw=2.0, color='green', ls='--')
# axs.plot(ion1t_x_vcd[:,0],  time_ns, lw=2.0, color='black')
# axs.plot(ion1t_x_vcd[:,2],  time_ns, lw=2.0, color='m')


axs.set_xlim([-4,4])
axs.set_ylim([0,4])
axs.set_aspect(1)

fig.set_size_inches(width,height)
fig.tight_layout()



In [73]:
# From this point, the post-process will become quite customized.
# It will be highly dependent on what you want to show.

# For case SS_v2_0_r0

# Draw the figure of x-t-ni/Bz
width = 3.2 * 3
height = width / 1.618
fig, axs = plt.subplots()

# cs1 = axs.pcolormesh(Bz_x_cd2, Bz_t_cd2, np.log10(Bz_cd2**2),cmap=plt.cm.Greys)
# cs1 = axs.pcolormesh(Bz_x_cd2, Bz_t_cd2, Bz_cd2,cmap=newcmap,vmin=0,vmax=200)
cs1 = axs.pcolormesh(Ey2_x_cd2, Ey2_t_cd2, Ey2_cd2/1e8,cmap='seismic',
                     vmin=-1.5,vmax=1.5
                     )

# cs1 = axs.pcolormesh(ni_x, ni_t, ni,cmap=plt.cm.jet)#,vmin=0,vmax=6.0e18)
# cs1 = axs.pcolormesh(ni_x_cd, ni_t_cd, ni_cd,cmap=newcmap,
#                      vmin=0,vmax=25.0
#                      )
# cs1.cmap.set_under(color='white')
# cs1.cmap.set_over(color='black')
cs1.cmap.set_under(color='blue')
cs1.cmap.set_over(color='red')
ax1_divider = make_axes_locatable(axs)
cax1=ax1_divider.append_axes("right", size="4%", pad="2%")
# cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$log_{10}(|B_z|^2)$')
# cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$B_z$ (T)')
cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$E_y$ (1e8 V/m)')
# cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$n_i$ (1e18 cm$^{-3}$)')
cbar1.ax.tick_params()
cax1.xaxis.set_ticks_position("top")
axs.tick_params(axis='both')
axs.set_xlabel('x (mm)')
axs.set_ylabel('t (ns)')

# axs.plot(ion2t_x_vcd[:,0:46:4],  time_ns, lw=2.0, ls='--')
# axs.plot(ion1t_x_vcd[:,0:111:10],  time_ns, lw=2.0)

# # axs.plot(ion2t_x_frame[:,0],  time_ns, lw=2.0, color='blue',   ls='--')
# # axs.plot(ion2t_x_frame[:,7],  time_ns, lw=2.0, color='red',  ls='--')
# # axs.plot(ion2t_x_frame[:,14], time_ns, lw=2.0, color='green', ls='--')
# # axs.plot(ion1t_x_frame[:,0],  time_ns, lw=2.0, color='black')
# # axs.plot(ion1t_x_frame[:,2],  time_ns, lw=2.0, color='m')

# # axs.plot(ion2t_x_vcd[:,0],  time_ns, lw=2.0, color='blue',   ls='--')
# axs.plot(ion2t_x_vcd[:,7],  time_ns, lw=2.0, color='red',  ls='--')
# # axs.plot(ion2t_x_vcd[:,14], time_ns, lw=2.0, color='green', ls='--')
# axs.plot(ion1t_x_vcd[:,0],  time_ns, lw=2.0, color='black')
# axs.plot(ion1t_x_vcd[:,2],  time_ns, lw=2.0, color='m')


axs.set_xlim([-4,4])
axs.set_ylim([0,4])
axs.set_aspect(1)

fig.set_size_inches(width,height)
fig.tight_layout()



In [74]:
width = 3.2 * 2
height = width / 1.618
fig, axs = plt.subplots()
part_id = 3
# axs.plot(ion2t_x_frame[:,0],  ion2t_E[:,0],  lw=2.0, ls='--', color='blue')
# axs.plot(ion2t_x_frame[:,7],  ion2t_E[:,7],  lw=2.0, ls='--', color='red')
# axs.plot(ion2t_x_frame[:,14], ion2t_E[:,14], lw=2.0, ls='--', color='green')
# axs.plot(ion1t_x_frame[:,0],  ion1t_E[:,0],  lw=2.0, color='black')
# axs.plot(ion1t_x_frame[:,2],  ion1t_E[:,2],  lw=2.0, color='m')

# axs.plot(ion2t_x_vcd[:,0],  ion2t_E[:,0],  lw=2.0, color='blue',   ls='--')
# axs.plot(ion2t_x_vcd[:,7],  ion2t_E[:,7],  lw=2.0, color='red',  ls='--')
# axs.plot(ion2t_x_vcd[:,14], ion2t_E[:,14], lw=2.0, color='green', ls='--')
# axs.plot(ion1t_x_vcd[:,0],  ion1t_E[:,0],  lw=2.0, color='black')
# axs.plot(ion1t_x_vcd[:,3],  ion1t_E[:,3],  lw=2.0, color='m')

# axs.plot(ion2t_x_vcd[:,0],  ion2t_E[:,0],  lw=2.0, color='blue',   ls='--')
# axs.plot(ion2t_x_vcd[:,7],  ion2t_E[:,7],  lw=2.0, color='red',  ls='--')
# axs.plot(ion2t_x_vcd[:,14], ion2t_E[:,14], lw=2.0, color='green', ls='--')
axs.plot(ion1t_x[:,part_id],  ion1t_px[:,part_id]*(me*c)/mp/1e3,  lw=2.0, color='blue', label=r'$V_x$')
axs.plot(ion1t_x[:,part_id],  ion1t_py[:,part_id]*(me*c)/mp/1e3,  lw=2.0, color='red', label=r'$V_y$')
# axs.plot(ion1t_x_vcd[:,3],  ion1t_E[:,3],  lw=2.0, color='m')

# axs.set_xlim([-2,2])
# axs.set_ylim([0,0.08])
axs.legend()
axs.set_xlabel('x [mm]')
axs.set_ylabel('v [km/s]')

Text(0, 0.5, 'v [km/s]')

In [76]:
width = 3.2 * 2
height = width 
fig, axs = plt.subplots()

id2 = 0

# axs.plot(ion2t_px_vcd[:,0],  ion2t_py[:,0],  lw=2.0, ls='--', color='blue')
axs.plot(ion2t_px[:1400,id2]*(me*c)/mp/1e3,  ion2t_py[:1400,id2]*(me*c)/mp/1e3,  lw=2.0, ls='--', color='red')
# axs.plot(ion2t_px[:,14], ion2t_py[:,14], lw=2.0, ls='--', color='green')
axs.plot(ion1t_px[:,0]*(me*c)/mp/1e3,  ion1t_py[:,0]*(me*c)/mp/1e3,  lw=2.0, color='black')
axs.plot(ion1t_px[:,0]*(me*c)/mp/1e3,  ion1t_py[:,0]*(me*c)/mp/1e3,  lw=2.0, color='m')

# axs.plot(ion2t_x_vcd[:,0],  ion2t_px[:,0],  lw=2.0, color='blue',   ls='--')
# axs.plot(ion2t_x_vcd[:,7],  ion2t_px[:,7],  lw=2.0, color='red',  ls='--')
# axs.plot(ion2t_x_vcd[:,14], ion2t_px[:,14], lw=2.0, color='green', ls='--')
# axs.plot(ion1t_x_vcd[:,0],  ion1t_px[:,0],  lw=2.0, color='black')
# # axs.plot(ion1t_x_vcd[:,3],  ion1t_px[:,3],  lw=2.0, color='m')
# axs.plot(ion1t_x_vcd[:,0],  ion1t_py[:,0],  lw=2.0, color='black', ls='--')

# axs.plot(time_ns,  ion1t_px[:,0],  lw=2.0, color='black')
# # axs.plot(ion1t_x_vcd[:,3],  ion1t_px[:,3],  lw=2.0, color='m')
# axs.plot(time_ns,  ion1t_py[:,0],  lw=2.0, color='black', ls='--')

# axs.plot(time_ns,  ion2t_px[:,0],  lw=2.0, color='blue',   ls='-')
# axs.plot(time_ns,  ion2t_py[:,0],  lw=2.0, color='blue',   ls='--')

# axs.plot(ion1t_px[:,0],  ion1t_py[:,0],  lw=2.0, color='black')


axs.set_xlim([-4000,6000])
axs.set_ylim([-5000,5000])
axs.grid()

axs.set_xlabel(r'$V_x (km/s)$')
axs.set_ylabel(r'$V_y (km/s)$')
axs.set_aspect('equal')
fig.tight_layout()

fig.set_size_inches(width,height)

In [ ]:
fig.savefig('/Users/yao/Desktop/'+'trace_vxvy2'+'.png',bbox_inches='tight',dpi=600)

In [77]:
# Draw the figure of x-t-ni-E

width = 3.2 * 2.5
height = width / 1.618 
fig, axs = plt.subplots()

# cs1 = axs.pcolormesh(Bz_x_cd2, Bz_t_cd2, np.log10(Bz_cd2**2),cmap=plt.cm.Greys)
cs1 = axs.pcolormesh(Ey1_x_cd2, Ey1_t_cd2, Ey1_cd2/1e8,cmap='seismic',
                     vmin=-1.5,vmax=1.5
                     )
# cs1 = axs.pcolormesh(ni_x, ni_t, ni,cmap=plt.cm.Greys,vmin=0,vmax=6.0e18)
# cs1 = axs.pcolormesh(ni_x_cd, ni_t_cd, ni_cd,cmap=plt.cm.Greys,vmin=0,vmax=16)
cs1.cmap.set_under(color='blue')
cs1.cmap.set_over(color='red')
ax1_divider = make_axes_locatable(axs)
cax1=ax1_divider.append_axes("right", size="4%", pad="2%")
# cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$log_{10}(|B_z|^2)$')
cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$E_y$ (1e8 V/m)')
# cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$n_i \ [1e18 \ cm^{-3}]$ ')
cbar1.ax.tick_params()
cax1.xaxis.set_ticks_position("top")
axs.tick_params(axis='both')
axs.set_xlabel('x (mm)')#,fontsize=18)
axs.set_ylabel('t (ns)')#,fontsize=18)

axs.set_xlim([-4,4])
axs.set_ylim([0,4])

cmap0 = plt.cm.viridis

id = 1
points = np.array([ion1t_x_vcd_DS[:,id], ion1t_time_ns_DS]).T.reshape(-1, 1, 2)
segments = np.concatenate([points[:-1], points[1:]], axis=1)
# norm = plt.Normalize(ion1t_E_DS[:,id].min()*1e3, ion1t_E_DS[:,id].max()*1e3)
norm = plt.Normalize(0, 500)
lc = LineCollection(segments, norm=norm,cmap=cmap0)
lc.set_array(ion1t_E_DS[:,id]*1e3)
lc.set_linewidth(3)
line = axs.add_collection(lc)

id = 0
points2 = np.array([ion2t_x_vcd_DS[:,id], ion2t_time_ns_DS]).T.reshape(-1, 1, 2)
segments2 = np.concatenate([points2[:-1], points2[1:]], axis=1)
# norm = plt.Normalize(ion2t_E_DS[:,id].min(), ion2t_E_DS[:,id].max())
lc2 = LineCollection(segments2, norm=norm,cmap=cmap0)
lc2.set_array(ion2t_E_DS[:,id]*1e3)
lc2.set_linewidth(3)
line = axs.add_collection(lc2)

id = 3
points3 = np.array([ion2t_x_vcd_DS[:,id], ion2t_time_ns_DS]).T.reshape(-1, 1, 2)
segments3 = np.concatenate([points3[:-1], points3[1:]], axis=1)

# norm3 = plt.Normalize(ion1t_E[:,id].min(), ion1t_E[:,id].max())
lc3 = LineCollection(segments3, norm=norm,cmap=cmap0)
# Set the values used for colormapping
lc3.set_array(ion2t_E_DS[:,id]*1e3)
lc3.set_linewidth(3)
line3 = axs.add_collection(lc3)

id = 2
points4= np.array([ion3t_x_vcd_DS[:,id], ion3t_time_ns_DS]).T.reshape(-1, 1, 2)
segments4 = np.concatenate([points4[:-1], points4[1:]], axis=1)

# norm4 = plt.Normalize(ion1t_E[:,id].min(), ion1t_E[:,id].max())
lc4 = LineCollection(segments4, norm=norm,cmap=cmap0)
# Set the values used for colormapping
lc4.set_array(ion3t_E_DS[:,id]*1e3)
lc4.set_linewidth(3)
line4 = axs.add_collection(lc4)

cax0=fig.add_axes([0.12,0.93,0.72,0.02])
cbar0=fig.colorbar(lc, ax=fig, cax=cax0, orientation="horizontal")
cbar0.ax.tick_params()
cax0.xaxis.set_ticks_position("bottom")
cbar0.ax.set_title('E (keV)')#,fontsize=18)

# fig.tight_layout()
fig.set_size_inches(width, height)

# fig.savefig('/Users/yz/Desktop/'+'trace_latest1'+'.png',bbox_inches='tight',dpi=300)

In [116]:
fig.savefig('/Users/yao/Desktop/'+'trace_DS'+'.png',bbox_inches='tight',dpi=600)

In [78]:
# Draw the figure of x-t-ni-E

width = 3.2 * 2.5
height = width / 1.618 
fig, axs = plt.subplots()

# cs1 = axs.pcolormesh(Bz_x_cd2, Bz_t_cd2, np.log10(Bz_cd2**2),cmap=plt.cm.Greys)
cs1 = axs.pcolormesh(Ey0_x_cd2, Ey0_t_cd2, Ey0_cd2/1e8,cmap='seismic',
                     vmin=-1.5,vmax=1.5
                     )
# cs1 = axs.pcolormesh(ni_x, ni_t, ni,cmap=plt.cm.Greys,vmin=0,vmax=6.0e18)
# cs1 = axs.pcolormesh(ni_x_cd, ni_t_cd, ni_cd,cmap=plt.cm.Greys,vmin=0,vmax=16)
cs1.cmap.set_under(color='blue')
cs1.cmap.set_over(color='red')
ax1_divider = make_axes_locatable(axs)
cax1=ax1_divider.append_axes("right", size="4%", pad="2%")
# cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$log_{10}(|B_z|^2)$')
cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$E_y$ (1e8 V/m)')
# cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$n_i \ [1e18 \ cm^{-3}]$ ')
cbar1.ax.tick_params()
cax1.xaxis.set_ticks_position("top")
axs.tick_params(axis='both')
axs.set_xlabel('x (mm)')#,fontsize=18)
axs.set_ylabel('t (ns)')#,fontsize=18)

axs.set_xlim([-4,4])
axs.set_ylim([0,4])

cmap0 = plt.cm.viridis

id = 1
points = np.array([ion1t_x_vcd[:,id], ion1t_time_ns]).T.reshape(-1, 1, 2)
segments = np.concatenate([points[:-1], points[1:]], axis=1)
# norm = plt.Normalize(ion1t_E[:,id].min()*1e3, ion1t_E[:,id].max()*1e3)
norm = plt.Normalize(0, 250)
lc = LineCollection(segments, norm=norm,cmap=cmap0)
lc.set_array(ion1t_E[:,id]*1e3)
lc.set_linewidth(3)
line = axs.add_collection(lc)

id = 0
points2 = np.array([ion2t_x_vcd[:,id], ion2t_time_ns]).T.reshape(-1, 1, 2)
segments2 = np.concatenate([points2[:-1], points2[1:]], axis=1)
# norm = plt.Normalize(ion2t_E_DS[:,id].min(), ion2t_E_DS[:,id].max())
lc2 = LineCollection(segments2, norm=norm,cmap=cmap0)
lc2.set_array(ion2t_E[:,id]*1e3)
lc2.set_linewidth(3)
line = axs.add_collection(lc2)

id = 2
points3 = np.array([ion2t_x_vcd[:,id], ion2t_time_ns]).T.reshape(-1, 1, 2)
segments3 = np.concatenate([points3[:-1], points3[1:]], axis=1)

# norm3 = plt.Normalize(ion1t_E[:,id].min(), ion1t_E[:,id].max())
lc3 = LineCollection(segments3, norm=norm,cmap=cmap0)
# Set the values used for colormapping
lc3.set_array(ion2t_E[:,id]*1e3)
lc3.set_linewidth(3)
line3 = axs.add_collection(lc3)

# id = 1
# points4= np.array([ion3t_x_vcd[:,id], ion3t_time_ns]).T.reshape(-1, 1, 2)
# segments4 = np.concatenate([points4[:-1], points4[1:]], axis=1)

# # norm4 = plt.Normalize(ion1t_E[:,id].min(), ion1t_E[:,id].max())
# lc4 = LineCollection(segments4, norm=norm,cmap=cmap0)
# # Set the values used for colormapping
# lc4.set_array(ion3t_E[:,id]*1e3)
# lc4.set_linewidth(3)
# line4 = axs.add_collection(lc4)

cax0=fig.add_axes([0.12,0.93,0.72,0.02])
cbar0=fig.colorbar(lc, ax=fig, cax=cax0, orientation="horizontal")
cbar0.ax.tick_params()
cax0.xaxis.set_ticks_position("bottom")
cbar0.ax.set_title('E (keV)')#,fontsize=18)

# fig.tight_layout()
fig.set_size_inches(width, height)

# fig.savefig('/Users/yz/Desktop/'+'trace_latest1'+'.png',bbox_inches='tight',dpi=300)

In [114]:
fig.savefig('/Users/yao/Desktop/'+'trace_SS'+'.png',bbox_inches='tight',dpi=600)

In [117]:
# Draw the figure of x-t-ni-E

width = 3.2 * 2.5
height = width / 1.618 
fig, axs = plt.subplots()

# cs1 = axs.pcolormesh(Bz_x_cd2, Bz_t_cd2, np.log10(Bz_cd2**2),cmap=plt.cm.Greys)
cs1 = axs.pcolormesh(Ey1_x_cd2, Ey1_t_cd2, Ey1_cd2/1e8,cmap='seismic',
                     vmin=-2.5,vmax=2.5
                     )
# cs1 = axs.pcolormesh(ni_x, ni_t, ni,cmap=plt.cm.Greys,vmin=0,vmax=6.0e18)
# cs1 = axs.pcolormesh(ni_x_cd, ni_t_cd, ni_cd,cmap=plt.cm.Greys,vmin=0,vmax=16)
cs1.cmap.set_under(color='blue')
cs1.cmap.set_over(color='red')
ax1_divider = make_axes_locatable(axs)
cax1=ax1_divider.append_axes("right", size="4%", pad="2%")
# cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$log_{10}(|B_z|^2)$')
cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$E_y$ (1e8 V/m)')
# cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$n_i \ [1e18 \ cm^{-3}]$ ')
cbar1.ax.tick_params()
cax1.xaxis.set_ticks_position("top")
axs.tick_params(axis='both')
axs.set_xlabel('x (mm)')#,fontsize=18)
axs.set_ylabel('t (ns)')#,fontsize=18)

# axs.set_xlim([-4,4])
# axs.set_ylim([0,4])

axs.set_xlim([-7,7])
axs.set_ylim([0,2.5])

cmap0 = plt.cm.PiYG



id = 1
points = np.array([ion1t_x_vcd_DS[:,id], ion1t_time_ns_DS]).T.reshape(-1, 1, 2)
segments = np.concatenate([points[:-1], points[1:]], axis=1)
# norm = plt.Normalize(ion1t_py_DS[:,id].min()*me*c/mp/1e3, ion1t_py_DS[:,id].max()*me*c/mp/1e3)
norm = plt.Normalize(-8, 8)
lc = LineCollection(segments, norm=norm,cmap=cmap0)
lc.set_array(ion1t_py_DS[:,id]*me*c/mp/1e6)
lc.set_linewidth(3)
line = axs.add_collection(lc)

id = 0
points2 = np.array([ion2t_x_vcd_DS[:,id], ion2t_time_ns_DS]).T.reshape(-1, 1, 2)
segments2 = np.concatenate([points2[:-1], points2[1:]], axis=1)
# norm = plt.Normalize(ion2t_E_DS[:,id].min(), ion2t_E_DS[:,id].max())
lc2 = LineCollection(segments2, norm=norm,cmap=cmap0)
lc2.set_array(ion2t_py_DS[:,id]*me*c/mp/1e6)
lc2.set_linewidth(3)
line = axs.add_collection(lc2)

id = 3
points3 = np.array([ion2t_x_vcd_DS[:,id], ion2t_time_ns_DS]).T.reshape(-1, 1, 2)
segments3 = np.concatenate([points3[:-1], points3[1:]], axis=1)

# norm3 = plt.Normalize(ion1t_E[:,id].min(), ion1t_E[:,id].max())
lc3 = LineCollection(segments3, norm=norm,cmap=cmap0)
# Set the values used for colormapping
lc3.set_array(ion2t_py_DS[:,id]*me*c/mp/1e6)
lc3.set_linewidth(3)
line3 = axs.add_collection(lc3)

id = 2
points4= np.array([ion3t_x_vcd_DS[:,id], ion3t_time_ns_DS]).T.reshape(-1, 1, 2)
segments4 = np.concatenate([points4[:-1], points4[1:]], axis=1)

# norm4 = plt.Normalize(ion1t_E[:,id].min(), ion1t_E[:,id].max())
lc4 = LineCollection(segments4, norm=norm,cmap=cmap0)
# Set the values used for colormapping
lc4.set_array(ion3t_py_DS[:,id]*me*c/mp/1e6)
lc4.set_linewidth(3)
line4 = axs.add_collection(lc4)

cax0=fig.add_axes([0.12,0.93,0.72,0.02])
cbar0=fig.colorbar(lc, ax=fig, cax=cax0, orientation="horizontal")
cbar0.ax.tick_params()
cax0.xaxis.set_ticks_position("bottom")
cbar0.ax.set_title(r'$V_y$ (1e6 m/s)')#,fontsize=18)

# fig.tight_layout()
fig.set_size_inches(width, height)

# fig.savefig('/Users/yz/Desktop/'+'trace_latest1'+'.png',bbox_inches='tight',dpi=300)

In [118]:
fig.savefig('/Users/yao/Desktop/'+'Vy_Ey_DS'+'.png',bbox_inches='tight',dpi=600)

In [110]:
# Draw the figure of x-t-ni-E

width = 3.2 * 2.5
height = width / 1.618 
fig, axs = plt.subplots()

# cs1 = axs.pcolormesh(Bz_x_cd2, Bz_t_cd2, np.log10(Bz_cd2**2),cmap=plt.cm.Greys)
cs1 = axs.pcolormesh(Ey0_x_cd2, Ey0_t_cd2, Ey0_cd2/1e8,cmap='seismic',
                     vmin=-2.5,vmax=2.5
                     )
# cs1 = axs.pcolormesh(ni_x, ni_t, ni,cmap=plt.cm.Greys,vmin=0,vmax=6.0e18)
# cs1 = axs.pcolormesh(ni_x_cd, ni_t_cd, ni_cd,cmap=plt.cm.Greys,vmin=0,vmax=16)
cs1.cmap.set_under(color='blue')
cs1.cmap.set_over(color='red')
ax1_divider = make_axes_locatable(axs)
cax1=ax1_divider.append_axes("right", size="4%", pad="2%")
# cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$log_{10}(|B_z|^2)$')
cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$E_y$ (1e8 V/m)')
# cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$n_i \ [1e18 \ cm^{-3}]$ ')
cbar1.ax.tick_params()
cax1.xaxis.set_ticks_position("top")
axs.tick_params(axis='both')
axs.set_xlabel('x (mm)')#,fontsize=18)
axs.set_ylabel('t (ns)')#,fontsize=18)

# axs.set_xlim([-4,4])
# axs.set_ylim([0,4])

axs.set_xlim([-7,7])
axs.set_ylim([0,2.5])

cmap0 = plt.cm.PiYG



id = 1
points = np.array([ion1t_x_vcd[:,id], ion1t_time_ns]).T.reshape(-1, 1, 2)
segments = np.concatenate([points[:-1], points[1:]], axis=1)
# norm = plt.Normalize(ion1t_py_DS[:,id].min()*me*c/mp/1e3, ion1t_py_DS[:,id].max()*me*c/mp/1e3)
norm = plt.Normalize(-2, 2)
lc = LineCollection(segments, norm=norm,cmap=cmap0)
lc.set_array(ion1t_py[:,id]*me*c/mp/1e6)
lc.set_linewidth(3)
line = axs.add_collection(lc)

id = 0
points2 = np.array([ion2t_x_vcd[:,id], ion2t_time_ns]).T.reshape(-1, 1, 2)
segments2 = np.concatenate([points2[:-1], points2[1:]], axis=1)
# norm = plt.Normalize(ion2t_E_DS[:,id].min(), ion2t_E_DS[:,id].max())
lc2 = LineCollection(segments2, norm=norm,cmap=cmap0)
lc2.set_array(ion2t_py[:,id]*me*c/mp/1e6)
lc2.set_linewidth(3)
line = axs.add_collection(lc2)

id = 1
points3 = np.array([ion3t_x_vcd[:,id], ion3t_time_ns]).T.reshape(-1, 1, 2)
segments3 = np.concatenate([points3[:-1], points3[1:]], axis=1)

# norm3 = plt.Normalize(ion1t_E[:,id].min(), ion1t_E[:,id].max())
lc3 = LineCollection(segments3, norm=norm,cmap=cmap0)
# Set the values used for colormapping
lc3.set_array(ion3t_py[:,id]*me*c/mp/1e6)
lc3.set_linewidth(3)
line3 = axs.add_collection(lc3)

# id = 2
# points4= np.array([ion3t_x_vcd[:,id], ion3t_time_ns]).T.reshape(-1, 1, 2)
# segments4 = np.concatenate([points4[:-1], points4[1:]], axis=1)

# # norm4 = plt.Normalize(ion1t_E[:,id].min(), ion1t_E[:,id].max())
# lc4 = LineCollection(segments4, norm=norm,cmap=cmap0)
# # Set the values used for colormapping
# lc4.set_array(ion3t_py_DS[:,id]*me*c/mp/1e6)
# lc4.set_linewidth(3)
# line4 = axs.add_collection(lc4)

cax0=fig.add_axes([0.12,0.93,0.72,0.02])
cbar0=fig.colorbar(lc, ax=fig, cax=cax0, orientation="horizontal")
cbar0.ax.tick_params()
cax0.xaxis.set_ticks_position("bottom")
cbar0.ax.set_title(r'$V_y$ (1e6 m/s)')#,fontsize=18)

# fig.tight_layout()
fig.set_size_inches(width, height)

# fig.savefig('/Users/yz/Desktop/'+'trace_latest1'+'.png',bbox_inches='tight',dpi=300)

In [111]:
fig.savefig('/Users/yao/Desktop/'+'Vy_Ey_SS1'+'.png',bbox_inches='tight',dpi=600)

In [115]:
# Draw the figure of x-t-ni-E

width = 3.2 * 2.5
height = width / 1.618 
fig, axs = plt.subplots()

# cs1 = axs.pcolormesh(Bz_x_cd2, Bz_t_cd2, np.log10(Bz_cd2**2),cmap=plt.cm.Greys)
cs1 = axs.pcolormesh(Ey2_x_cd2, Ey2_t_cd2, Ey2_cd2/1e8,cmap='seismic',
                     vmin=-5,vmax=5
                     )
# cs1 = axs.pcolormesh(ni_x, ni_t, ni,cmap=plt.cm.Greys,vmin=0,vmax=6.0e18)
# cs1 = axs.pcolormesh(ni_x_cd, ni_t_cd, ni_cd,cmap=plt.cm.Greys,vmin=0,vmax=16)
cs1.cmap.set_under(color='blue')
cs1.cmap.set_over(color='red')
ax1_divider = make_axes_locatable(axs)
cax1=ax1_divider.append_axes("right", size="4%", pad="2%")
# cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$log_{10}(|B_z|^2)$')
cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$E_y$ (1e8 V/m)')
# cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$n_i \ [1e18 \ cm^{-3}]$ ')
cbar1.ax.tick_params()
cax1.xaxis.set_ticks_position("top")
axs.tick_params(axis='both')
axs.set_xlabel('x (mm)')#,fontsize=18)
axs.set_ylabel('t (ns)')#,fontsize=18)

# axs.set_xlim([-4,4])
# axs.set_ylim([0,4])

axs.set_xlim([-7,7])
axs.set_ylim([0,2.5])

cmap0 = plt.cm.PiYG



id = 1
points = np.array([ion1t_x_vcd_SS2[:,id], ion1t_time_ns_SS2]).T.reshape(-1, 1, 2)
segments = np.concatenate([points[:-1], points[1:]], axis=1)
# norm = plt.Normalize(ion1t_py_DS[:,id].min()*me*c/mp/1e3, ion1t_py_DS[:,id].max()*me*c/mp/1e3)
norm = plt.Normalize(-8, 8)
lc = LineCollection(segments, norm=norm,cmap=cmap0)
lc.set_array(ion1t_py_SS2[:,id]*me*c/mp/1e6)
lc.set_linewidth(3)
line = axs.add_collection(lc)

id = 0
points2 = np.array([ion2t_x_vcd_SS2[:,id], ion2t_time_ns_SS2]).T.reshape(-1, 1, 2)
segments2 = np.concatenate([points2[:-1], points2[1:]], axis=1)
# norm = plt.Normalize(ion2t_E_DS[:,id].min(), ion2t_E_DS[:,id].max())
lc2 = LineCollection(segments2, norm=norm,cmap=cmap0)
lc2.set_array(ion2t_py_SS2[:,id]*me*c/mp/1e6)
lc2.set_linewidth(3)
line = axs.add_collection(lc2)

id = 1
points3 = np.array([ion3t_x_vcd_SS2[:,id], ion3t_time_ns_SS2]).T.reshape(-1, 1, 2)
segments3 = np.concatenate([points3[:-1], points3[1:]], axis=1)

# norm3 = plt.Normalize(ion1t_E[:,id].min(), ion1t_E[:,id].max())
lc3 = LineCollection(segments3, norm=norm,cmap=cmap0)
# Set the values used for colormapping
lc3.set_array(ion3t_py_SS2[:,id]*me*c/mp/1e6)
lc3.set_linewidth(3)
line3 = axs.add_collection(lc3)

# id = 2
# points4= np.array([ion3t_x_vcd[:,id], ion3t_time_ns]).T.reshape(-1, 1, 2)
# segments4 = np.concatenate([points4[:-1], points4[1:]], axis=1)

# # norm4 = plt.Normalize(ion1t_E[:,id].min(), ion1t_E[:,id].max())
# lc4 = LineCollection(segments4, norm=norm,cmap=cmap0)
# # Set the values used for colormapping
# lc4.set_array(ion3t_py_DS[:,id]*me*c/mp/1e6)
# lc4.set_linewidth(3)
# line4 = axs.add_collection(lc4)

cax0=fig.add_axes([0.12,0.93,0.72,0.02])
cbar0=fig.colorbar(lc, ax=fig, cax=cax0, orientation="horizontal")
cbar0.ax.tick_params()
cax0.xaxis.set_ticks_position("bottom")
cbar0.ax.set_title(r'$V_y$ (1e6 m/s)')#,fontsize=18)

# fig.tight_layout()
fig.set_size_inches(width, height)

# fig.savefig('/Users/yz/Desktop/'+'trace_latest1'+'.png',bbox_inches='tight',dpi=300)

In [116]:
fig.savefig('/Users/yao/Desktop/'+'Vy_Ey_SS2'+'.png',bbox_inches='tight',dpi=600)

In [ ]:
for i in range(111):
    print(i, np.max(ion1t_E[:,i]))

In [ ]:
# Draw the figure of x-t-ni-Fx

# prepare Lorentz force
# Here, the Ex contribution is not small, but high-frequency.
# fx = qe * (ion2t_Ex[:,0]*me*wr*c/qe + ion2t_py[:,0]*me*c/mp * ion2t_Bz[:,0]*me*wr/qe)
fx = qe * (ion2t_py[:,0]*me*c/mp * ion2t_Bz[:,0]*me*wr/qe)
fy = qe * (ion2t_px[:,0]*me*c/mp * ion2t_Bz[:,0]*me*wr/qe) * -1.0

# Prepare the work done by Lorentz force
xx  = ion2t_x[:,0] * de
# ddx = zeros_like(xx)
# wx  = zeros_like(xx)
# for i in range(xx.size-1):
#     ddx[i+1] = xx[i+1] - xx[i]
#     wx[i+1]  = wx[i] + fx[i+1] * ddx[i+1]
wx = fx * xx
wx_norm = wx / wx.max()
wx_mev = wx / qe / 1e6  # convert it into MeV
# dde = zeros_like(ion2t_E[:,0])
# for i in range(dde.size-1):
#     dde[i+1] = ion2t_E[i+1,0] - ion2t_E[i,0]

width = 3.2 * 3
height = width / 1.618 / 2 
fig, axs = plt.subplots()

# cs1 = axs.pcolormesh(Bz_x, Bz_t, np.log10(Bz**2),cmap=plt.cm.Greys)
# cs1 = axs.pcolormesh(ni_x, ni_t, ni,cmap=plt.cm.Greys,vmin=0,vmax=6.0e18)
cs1 = axs.pcolormesh(ni_x_cd, ni_t_cd, ni_cd,cmap=plt.cm.Greys,vmin=0,vmax=16)
# cs1 = axs.pcolormesh(ni_x_0, ni_t_0, ni_0,cmap=plt.cm.Greys,vmin=0,vmax=6.0e18)
cs1.cmap.set_under(color='white')
cs1.cmap.set_over(color='black')
ax1_divider = make_axes_locatable(axs)
cax1=ax1_divider.append_axes("right", size="4%", pad="2%")
# cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$log_{10}(|B_z|^2)$')
cbar1=fig.colorbar(cs1, ax=fig, cax=cax1, orientation="vertical", label=r'$n_i\ (1e18\ cm^{-3})$ ')
cbar1.ax.tick_params()
cax1.xaxis.set_ticks_position("top")
axs.tick_params(axis='both')
axs.set_xlabel('x (mm)')
axs.set_ylabel('t (ns)')

axs.set_xlim([-2,1])
axs.set_ylim([0,2])

# points = np.array([ion2t_x_frame[:,0], time_ns]).T.reshape(-1, 1, 2)
points = np.array([ion2t_x_vcd[:,0], time_ns]).T.reshape(-1, 1, 2)
# points = np.array([ion2t_x[:,0]*de*1e3, time_ns]).T.reshape(-1, 1, 2)
segments = np.concatenate([points[:-1], points[1:]], axis=1)

norm = plt.Normalize(-1.0, 1.0)
# norm = plt.Normalize(ion2t_E[:,0].min(), ion2t_E[:,0].max())
lc = LineCollection(segments, norm=norm,cmap=plt.cm.seismic)
# lc = LineCollection(segments, norm=norm,cmap=newcmap)
# Set the values used for colormapping
# lc.set_array(dde)
lc.set_array(wx_norm)
lc.set_linewidth(5)
line = axs.add_collection(lc)

cax0=fig.add_axes([0.12,0.93,0.72,0.02])
cbar0=fig.colorbar(lc, ax=fig, cax=cax0, orientation="horizontal")
cbar0.ax.tick_params()
cax0.xaxis.set_ticks_position("bottom")
cbar0.ax.set_title('Wx (A.U.)',fontsize=18)
# cbar0.ax.set_title('Fx [kgm/s2]',fontsize=18)
# fig.set_size_inches(width, height)

In [ ]:
plt.plot(ni_cd[100,:])

In [ ]:
ion1t_1d = 50

ion1t_Fx  = ion1t_Ex[:,ion1t_id] + ion1t_py[:,ion1t_id] * ion1t_Bz[:,ion1t_id]
ion1t_Fx1 = ion1t_Ex[:,ion1t_id] 
ion1t_Fx2 = ion1t_py[:,ion1t_id] * ion1t_Bz[:,ion1t_id]

ion1t_Fy  = ion1t_Ey[:,ion1t_id] - ion1t_px[:,ion1t_id] * ion1t_Bz[:,ion1t_id]
ion1t_Fy1 = ion1t_Ey[:,ion1t_id] 
ion1t_Fy2 = -1.0 * ion1t_px[:,ion1t_id] * ion1t_Bz[:,ion1t_id]

ion2t_Fx  = ion2t_Ex[:,ion2t_id] + ion2t_py[:,ion2t_id] * ion2t_Bz[:,ion2t_id]
ion2t_Fx1 = ion2t_Ex[:,ion2t_id] 
ion2t_Fx2 = ion2t_py[:,ion2t_id] * ion2t_Bz[:,ion2t_id]

ion2t_Fy  = ion2t_Ey[:,ion2t_id] - ion2t_px[:,ion2t_id] * ion2t_Bz[:,ion2t_id]
ion2t_Fy1 = ion2t_Ey[:,ion2t_id] 
ion2t_Fy2 = -1.0 * ion2t_px[:,ion2t_id] * ion2t_Bz[:,ion2t_id]

In [ ]:
fig, ax = plt.subplots()

ax.plot(ion1t_x[:,ion1t_id]*de*1e3, ion1t_Fx/(me*c*wr)/1e8, color='red', lw=2.0, label='Fx')
ax.plot(ion1t_x[:,ion1t_id]*de*1e3, ion1t_Fy/(me*c*wr)/1e8, color='blue', lw=2.0, label='Fy')
ax.plot(ion1t_x[:,ion1t_id]*de*1e3, ion1t_time_ns/wr*1e9, color='black', lw=2.0, label='trajectory')
ax.set_xlabel('position x (mm)')
ax.set_ylabel('Lorentz force (normed)')
ax.legend()
ax.grid()
fig.tight_layout()
plt.show()

In [ ]:
ion1t_Fx.size

In [ ]:
ion1t_W  = np.zeros_like(ion1t_Fx)

for i in range(ion1t_Fx.size-1):
    ion1t_W[i+1]  = ion1t_W[i]  + (ion1t_Fx[i+1]+ion1t_Fx[i])/2.  * (ion1t_x[i+1,ion1t_id] - ion1t_x[i,ion1t_id])*1e-3/de
#     ion1t_W[i+1]  = ion1t_W[i+1]  + ion1t_Fx[i+1]  * (ion1t_x[i+1,ion1t_id] - ion1t_x[i,ion1t_id])*1e-3/de


ion2t_W  = np.zeros_like(ion2t_Fx)

for i in range(ion1t_Fx.size-1):
    ion2t_W[i+1]  = ion2t_W[i]  + (ion2t_Fx[i+1]+ion2t_Fx[i])/2.  * (ion2t_x[i+1,ion2t_id] - ion2t_x[i,ion2t_id])*1e-3/de



In [ ]:
fig, ax1 = plt.subplots()

color = 'tab:red'
ax1.set_xlabel('position x (mm)')
# ax1.set_xlabel('time (ns)')
ax1.set_ylabel('Work done by Fx', color=color)
ax1.set_ylim(ion1t_W1.min(),-ion1t_W1.min())
ax1.plot(ion1t_x[:,ion1t_id], ion1t_W1, color=color, lw=2.0, label='All')
# ax1.plot(ion1t_x[:,ion1t_id], ion1t_Fx1, color=color, lw=2.0, ls='--', label='Ex')
# ax1.plot(ion1t_x[:,ion1t_id], ion1t_Fx2, color=color, lw=2.0, ls='-.', label='vyBz')
# ax1.plot(ion1t_time_ns, ion1t_E_sub, color=color)
ax1.tick_params(axis='y',labelcolor=color)
ax1.grid()
ax2 = ax1.twinx()


dEx = ion1t_px[:,ion1t_id]**2 / 2.0 / mp / qe / 1e6
dEy = ion1t_py[:,ion1t_id]**2 / 2.0 / mp / qe / 1e6
dEz = ion1t_pz[:,ion1t_id]**2 / 2.0 / mp / qe / 1e6
color= 'tab:blue'
ax2.set_ylabel(r'$\delta E$', color=color)
ax2.set_ylim(0,dEx.max())
ax2.plot(ion1t_x[:,ion1t_id], dEx, color=color, lw=2.0, ls='-',  label=r'$\delta E_x$')
ax2.plot(ion1t_x[:,ion1t_id], dEy, color='black', lw=2.0, ls='-',  label=r'$\delta E_y$')
# ax2.plot(ion1t_x[:,ion1t_id], dEz, color='green', lw=2.0, ls='-',  label=r'$\delta E_z$')
# ax1.plot(ion1t_x[:,ion1t_id], ion1t_Fy1, color=color, lw=2.0, ls='--', label='Ey')
# ax1.plot(ion1t_x[:,ion1t_id], ion1t_Fy2, color=color, lw=2.0, ls='-.', label='vxBz')
ax2.tick_params(axis='y', labelcolor=color)
ax2.legend()
fig.tight_layout()
plt.show()


# # plt.plot(ion1t_x[:,ion1t_id], ion1t_W, '-k', lw=2.0, label='Work done by Fx')
# plt.plot(ion1t_time_ns,ion1t_W)
# plt.plot(ion1t_time_ns,ion1t_E_sub)
# plt.xlabel('position x (mm)')
# plt.ylabel('Work done by Lorentz force (Arb. Unit)')
# plt.legend()

In [14]:
# ion x-px
xpx0 = S0.ParticleBinning(0,units=['mm', 'ns', '1000 km/s'],
                  data_log=True,
                   # xmin=5,
                   # xmax=11,
                   ymin=-10,
                   ymax=10,
                  # vmin=-1,
                  # vmax=4,
                  cmap=newcmap
                  # ).animate(movie='/Users/yao/Desktop/xpx_i_t1.gif')
                  )#.slide()

xpx1 = S1.ParticleBinning(0,units=['mm', 'ns', '1000 km/s'],
                  data_log=True,
                   # xmin=5,
                   # xmax=11,
                   ymin=-10,
                   ymax=10,
                  # vmin=-1,
                  # vmax=4,
                  cmap=newcmap
                  # ).animate(movie='/Users/yao/Desktop/xpx_i_t1.gif')
                  )#.slide()

happi.multiSlide(xpx0, xpx1, shape=[2,1])

/Users/yao/Smilei/happi/_Diagnostics/Diagnostic.py:857: RuntimeWarning: divide by zero encountered in log10
  return self._np.log10( self._dataLinAtTime(t) )


In [10]:
# ion x
S0.ParticleBinning(0,units=['mm', 'ns', 'km/s','cm^-3'],
                  # data_log=True,
                   # sum={'vx':'all'},
                   # xmin=5,
                   # xmax=11,
                  # vmin=-2,
                  # vmax=4,
                  # cmap=newcmap
                  # ).animate(movie='/Users/yao/Desktop/x_i_t1.gif')
                  ).slide()


#0 - Number density of species # 0,3,6
    x from 0 to 6144 in 500 steps 
    vx from -0.05 to 0.05 in 500 steps 

The value in each bin is the sum of the `deposited_quantity` divided by the bin size



In [13]:
# eon x-px
S1.ParticleBinning(3,units=['mm', 'ns', 'km/s'],
                  data_log=True,
                  vmin=-2,
                  vmax=4,
                  cmap=newcmap
                  ).slide()


#3 - Number density of species # 2,5,8
    x from 0 to 6144 in 500 steps 
    ekin from 0 to 0.1 in 500 steps 

The value in each bin is the sum of the `deposited_quantity` divided by the bin size



/Users/yao/Smilei/happi/_Diagnostics/Diagnostic.py:857: RuntimeWarning: divide by zero encountered in log10
  return self._np.log10( self._dataLinAtTime(t) )


In [17]:
# ion spectrum
S0.ParticleBinning(2,units=['mm', 'ns', 'km/s','MeV'],
                  data_log=True,
                  # vmin=-2,
                  # vmax=4,
                   sum={'x':'all'},
                   # ymin=0,
                   # ymax=200,
                  cmap=newcmap
                  ).slide()


#2 - Number density of species # 0,3,6
    x from 0 to 6144 in 500 steps 
    ekin from 0 to 1 in 500 steps 

average for all x
The value in each bin is the sum of the `deposited_quantity` divided by the bin size



In [17]:
# eon spectrum
e0 = S0.ParticleBinning(3,units=['mm', 'ns', 'km/s','keV'],
                  data_log=True,
                  # vmin=-2,
                  # vmax=4,
                   sum={'x':'all'},
                   color='red',
                   linestyle='-',
                   label='7 bars',
                #    ymin=0,
                #    ymax=200,
                #   cmap=newcmap
                  )

e1 = S1.ParticleBinning(3,units=['mm', 'ns', 'km/s','keV'],
                  data_log=True,
                  # vmin=-2,
                  # vmax=4,
                   sum={'x':'all'},
                   color='blue',
                   linestyle='--',
                   label='3.5 bars',
                #    ymin=0,
                #    ymax=200,
                #   cmap=newcmap
                  )


happi.multiSlide(e0, e1)

/Users/yao/Smilei/happi/_Diagnostics/Diagnostic.py:857: RuntimeWarning: divide by zero encountered in log10
  return self._np.log10( self._dataLinAtTime(t) )


In [18]:
# ion vx-vy
S.ParticleBinning(4,units=['mm', 'ns', 'km/s'],
                  data_log=True,
                  vmin=-2,
                  vmax=6,
                  cmap=newcmap,
                   aspect='equal',
                  ).slide()

NameError: name 'S' is not defined

In [21]:
# eon vx-vy
S1.ParticleBinning(1,units=['mm', 'ns', 'km/s'],
                #   data_log=True,
                #   vmin=-2,
                #   vmax=6,
                  cmap=newcmap,
                #    aspect='equal',
                  ).slide()


#1 - Number density of species # 2,5,8
    x from 0 to 6144 in 500 steps 
    vx from -0.25 to 0.25 in 500 steps 

The value in each bin is the sum of the `deposited_quantity` divided by the bin size



In [ ]:
Bz = S.Field(0,'Bz',units=['mm','ns'],
         label='Bz',
              color='blue',
              linestyle='--',
             )
        # ).slide()

ni = S.ParticleBinning("#0*0.03",units=['mm', 'ns'],
                   sum={'vx':'all'},
                        label='ni',
                        color='red',
                       )
                  # ).slide()

happi.multiSlide(Bz, ni)

In [ ]:
Ex0 = S.Field(0,'Ex',units=['mm','ns','V/m'],
         label='Ex0',
              color='blue',
              linestyle='--',
             )

Ex1 = S.Field(1,'Ex',units=['mm','ns','V/m'],
         label='Ex0',
              color='red',
              linestyle='-',
             )

happi.multiSlide(Ex0,Ex1,
                 # shape=[1,3]
                )

In [ ]:
S.Field(0,'(Rho_ion1+Rho_ion2)',units=['mm','ns','T','cm^-3'],
         label='ion',
        ).slide()

In [ ]:
S.Field(0,'Bz',units=['mm','ns','T'],
         label='Bz',
         # xmin=5,
                   # xmax=11,
              # color='blue',
              # linestyle='--',
        ).streak()
             # ).animate(movie='/Users/yao/Desktop/bz_t1.gif')

In [ ]:
S.ParticleBinning("(#6+#8)/(#7+#9)", 
                   units=['mm','ns','cm^-3','km/s','eV'],
                   # xmin=5,
                   # xmax=11,
                  ).slide()


In [ ]:
S.ParticleBinning()

In [ ]:
S.ParticleBinning("(#10+#12)/(#11+#13)", 
                   units=['mm','ns','cm^-3','km/s','eV'],
                   # xmin=5,
                   # xmax=11,                   
                  ).slide()


In [ ]:
S.ParticleBinning(14, 
                   units=['mm','ns','cm^-3','1000 km/s','keV'],
                   data_log=True,
                   cmap=newcmap,
                   vmin=1,
                   vmax=5,
                   xmin=-6,
                   xmax=6,
                   ymin=-6,
                   ymax=6,
                   aspect=1
                  ).slide()

In [ ]:
# ion x-px
S.ParticleBinning(0,units=['mm', 'ns', '1000 km/s'],
                  data_log=True,
                   # xmin=5,
                   # xmax=11,
                   # ymin=-1,
                   # ymax=5,
                  # vmin=-1,
                  # vmax=4,
                  cmap=newcmap,
                   # aspect=1
                  # ).animate(movie='/Users/yao/Desktop/xpx_i_t1.gif')
                  ).slide()

In [22]:
import numpy as np
import matplotlib as mpl
# mpl.use('pdf')
import matplotlib.pyplot as plt

In [ ]:
plt.rc('font', family='sans-serif', serif='Arial')
plt.rc('text', usetex=True)
plt.rc('xtick', labelsize=12)
plt.rc('ytick', labelsize=12)
plt.rc('axes', labelsize=12)

In [ ]:
time = np.array([2, 3, 4, 6, 8, 10, 12]) # ns
size_on_screen = np.array([2.1, 2.69, 3, 5.37, 6.24, 7.15, 8.26]) # cm

def rescale(x):
    return x*17/6.79

In [ ]:
size_in_physics = rescale(size_on_screen) # in mm
print(size_in_physics)

In [ ]:
def lin_reg(x_data, y_data):
    n = np.size(x_data)
    
    xm = np.mean(x_data)
    ym = np.mean(y_data)
    S1 = np.sum(x_data*y_data) - n*xm*ym
    S2 = np.sum(x_data**2) - n*xm**2
    
    a1 = S1/S2
    a0 = ym - a1*xm
    
    return (a0,a1)

In [ ]:
a0_7bar, a1_7bar = lin_reg(time, size_in_physics/2.)

In [ ]:
width  = 3.487 
height = width / 1.618 * 1.5

fig, ax = plt.subplots()
fig.subplots_adjust(left=.15, bottom=.16, right=.99, top=.97)


x = np.linspace(time[0],time[-1],50)

ax.plot(x, a0_7bar+a1_7bar*x, 'b-',
        label='Expansion velocity v0 = {:.1e} km/s'.format(a1_7bar*1e3)
       )

ax.plot(time, size_in_physics/2., 'ro',
        label='Experimental data',
       )



ax.set_xlabel("Time (ns)")
ax.set_ylabel("Radius (mm)")
ax.set_xlim([time[0],time[-1]])
ax.set_ylim([2,12])
# ax.set_title('Expansion velocity v = {:.1e} m/s'.format(a1*1e3))
ax.legend()

fig.set_size_inches(width, height)



# fig.savefig('/Users/yao/Desktop/plot.pdf')

In [ ]:
fig.savefig('/Users/yao/Desktop/plot_7bars.pdf')

In [ ]:
# for pressure of 4 bars H2
x_data = np.array([3.0,   5.0,   6.0,   7.0,   8.0])
y_data = np.array([9.51, 13.97, 15.45, 18.38, 20.68])
a0,a1 = lin_reg(x_data,y_data/2.)

In [ ]:
width  = 3.487 
height = width / 1.618 * 1.5

fig, ax = plt.subplots()
fig.subplots_adjust(left=.15, bottom=.16, right=.99, top=.97)


x = np.linspace(2,10,50)

ax.plot(x, a0+a1*x, 'b-',
        label='Expansion velocity v0 = {:.1e} km/s'.format(a1*1e3)
       )

ax.plot(x_data,y_data/2.,'ro',
        label='Experimental data',
       )



ax.set_xlabel("Time (ns)")
ax.set_ylabel("Radius (mm)")
ax.set_xlim([3,8])
ax.set_ylim([4,12])
# ax.set_title('Expansion velocity v = {:.1e} m/s'.format(a1*1e3))
ax.legend()

fig.set_size_inches(width, height)



# fig.savefig('/Users/yao/Desktop/plot.pdf')

In [ ]:
fig.savefig('/Users/yao/Desktop/plot.pdf')

In [ ]:
a0

In [ ]:
# for pressure of 4 bars H2
x_data = np.array([3.0,   5.0,   6.0,   7.0,   8.0]) # time in ns
y_data = np.array([9.51, 13.97, 15.45, 18.38, 20.68]) # size (diameter) in mm

In [ ]:
0.015 * 3e8 /3

In [ ]:
4.5e-3 / 3e-9 * 1e-9 * 1e3

In [ ]:
condition_p1 = "any(t>0, ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.1) * ((px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 < 0.15))"


In [ ]:
(px**2+py**2+pz**2)*(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6 > 0.1

In [ ]:
(9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6

In [ ]:
0.1 / ((9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6)

In [ ]:
import numpy as np

In [ ]:
np.sqrt(1. / ((9.1e-31*3.0e8)**2/2./(1836*9.1e-31)/1.6e-19/1e6))

In [ ]:
me = 9.1e-31
c = 3e8

## experimental energy spectrum

In [12]:
from matplotlib import font_manager

font_dirs = ['/Users/yao/Documents/Calibri and Cambria Fonts/']
font_files = font_manager.findSystemFonts(fontpaths=font_dirs)

for font_file in font_files:
    font_manager.fontManager.addfont(font_file)

# set font
plt.rcParams['font.family'] = 'Calibri'

plt.rc('text', usetex=False)
plt.rc('xtick', labelsize=16)
plt.rc('ytick', labelsize=16)
plt.rc('axes', labelsize=16)
plt.rc('legend', fontsize=12)

width  = 3.487
height = width / 1.618 * 1.0

In [13]:
# double shots with magnetic field of 10 T

data_directory = '/Users/yao/Nextcloud/PROJECTS/Vulcan/RAL_August2023/spectra_more_data/'

# shot 98, 7 bars

ene_s98 = 1e3 * np.loadtxt(data_directory+'shot98.txt',usecols=0) # in keV
num_s98 =       np.loadtxt(data_directory+'shot98.txt',usecols=1) 

# shot 86, 7 bars also

ene_s86 = 1e3 * np.loadtxt(data_directory+'shot86.txt',usecols=0)  # in keV
num_s86 = np.loadtxt(data_directory+'shot86.txt',usecols=1)

# shot 94, 5 bars 

ene_s94 = 1e3 * np.loadtxt(data_directory+'shot94.txt',usecols=0)  # in keV
num_s94 = np.loadtxt(data_directory+'shot94.txt',usecols=1)

# shot 97, 4 bars 

ene_s97 = 1e3 * np.loadtxt(data_directory+'shot97.txt',usecols=0)  # in keV
num_s97 = np.loadtxt(data_directory+'shot97.txt',usecols=1)

# shot 95, 3 bars 

ene_s95 = 1e3 * np.loadtxt(data_directory+'shot95.txt',usecols=0)  # in keV
num_s95 = np.loadtxt(data_directory+'shot95.txt',usecols=1)


In [14]:
# single shots with magnetic field of 10 T

# shot 103, 7 bars

ene_s103 = 1e3 * np.loadtxt(data_directory+'shot103.txt',usecols=0) # in keV
num_s103 =       np.loadtxt(data_directory+'shot103.txt',usecols=1) 

# shot 87, 7 bars also

ene_s87 = 1e3 * np.loadtxt(data_directory+'shot87.txt',usecols=0)  # in keV
num_s87 = np.loadtxt(data_directory+'shot87.txt',usecols=1)

# # shot 94, 5 bars 

# ene_s94 = 1e3 * np.loadtxt(data_directory+'shot94.txt',usecols=0)  # in keV
# num_s94 = np.loadtxt(data_directory+'shot94.txt',usecols=1)

In [ ]:
exp_energy_B          = np.mean(np.stack((ene_s98, ene_s86, ene_s94)), axis=0)
exp_energy_B_xerr_min = np.stack((ene_s98, ene_s86, ene_s94)).min(axis=0)
exp_energy_B_xerr_max = np.stack((ene_s98, ene_s86, ene_s94)).max(axis=0)
exp_energy_B_xerr     = np.stack((np.abs(exp_energy_B_xerr_min - exp_energy_B), 
                                  np.abs(exp_energy_B_xerr_max - exp_energy_B))
                                ).min(axis=0)

exp_number_B          = np.mean(np.stack((num_s98, num_s86, num_s94)), axis=0)
exp_number_B_yerr_min = np.stack((num_s98, num_s86, num_s94)).min(axis=0)
exp_number_B_yerr_max = np.stack((num_s98, num_s86, num_s94)).max(axis=0)
exp_number_B_yerr     = np.stack((np.abs(exp_number_B_yerr_min - exp_number_B), 
                                  np.abs(exp_number_B_yerr_max - exp_number_B))
                                ).min(axis=0)

In [26]:
# provide you with the timesteps available

S1.ParticleBinning(2).getTimesteps()[136]

IndexError: index 136 is out of bounds for axis 0 with size 136

In [12]:
num = 101

print(S0.ParticleBinning(2).getTimesteps()[num])
print(S0.ParticleBinning(2,units=['ns']).getTimes()[num])

1683266
2.9858347651057433


In [13]:
num = 130

print(S1.ParticleBinning(2).getTimesteps()[num])
print(S1.ParticleBinning(2,units=['ns']).getTimes()[num])

2166580
3.8431536580568975


In [60]:
S1.ParticleBinning(2,units=['ns']).getTimes()[130]

3.8431536580568975

In [14]:
# add the simulation data onto the exp. spectra

# but here note that we need to be careful with the "time"

# time_snap = 1316614 # 2.3 ns
# time_snap = S1.ParticleBinning(2).getTimesteps()[133] # 4 ns

# ekin1, num1, t_end1 = spect_load_1d_iter(wkdir[1], time_snap, 2, 0.0, Lx)
# ekin0, num0, t_end0 = spect_load_1d_iter(wkdir[0], time_snap, 2, 0.0, Lx)

time_snap = S1.ParticleBinning(2).getTimesteps()[90] # 3 ns

ekin3, num3, t_end3 = spect_load_1d_iter(wkdir[1], time_snap, 2, 0.0, Lx)
ekin2, num2, t_end2 = spect_load_1d_iter(wkdir[0], time_snap, 2, 0.0, Lx)

# time_snap = S1.ParticleBinning(2).getTimesteps()[79] # 2.3 ns

# ekin5, num5, t_end5 = spect_load_1d_iter(wkdir[1], time_snap, 2, 0.0, Lx)
# ekin4, num4, t_end4 = spect_load_1d_iter(wkdir[0], time_snap, 2, 0.0, Lx)

Loaded simulation '/Users/yao/Desktop/Data/v2500/DS_11_v2500_r0/'
Loaded simulation '/Users/yao/Desktop/Data/v2500/DS_11_v2500_r1/'
Scanning for Scalar diagnostics
Scanning for Field diagnostics
Scanning for Probe diagnostics
Scanning for ParticleBinning diagnostics
Scanning for RadiationSpectrum diagnostics
Scanning for Performance diagnostics
Scanning for Screen diagnostics
Scanning for Tracked particle diagnostics
Scanning for new particle diagnostics
Loaded simulation '/Users/yao/Desktop/Data/v2500/SS_11_v2500_r0/'
Loaded simulation '/Users/yao/Desktop/Data/v2500/SS_11_v2500_r1/'
Scanning for Scalar diagnostics
Scanning for Field diagnostics
Scanning for Probe diagnostics
Scanning for ParticleBinning diagnostics
Scanning for RadiationSpectrum diagnostics
Scanning for Performance diagnostics
Scanning for Screen diagnostics
Scanning for Tracked particle diagnostics
Scanning for new particle diagnostics


In [19]:
# experiment

width  = 3.487 * 1.3
height = width / 1.618 * 1.2

fig, ax = plt.subplots()
fig.subplots_adjust(left=.15, bottom=.16, right=.99, top=.97)

ax.semilogy(ene_s98, num_s98,
            linestyle=' ',
            marker='o',markersize=3,mfc='orange',
            label='double, s98',
            markeredgecolor='orange',
            )

ax.semilogy(ene_s86, num_s86,
            linestyle=' ',
            marker='s',markersize=3,mfc='red',
            label='double, s86',
            markeredgecolor='red',
            )

# ax.semilogy(ene_s94, num_s94,
#             linestyle=' ',
#             marker='^',markersize=4,mfc='none',
#             label='s94',
#             markeredgecolor='m',
#             )

ax.semilogy(ene_s103, num_s103,
            linestyle=' ',
            marker='X',markersize=5,
            # mfc='c',
            mfc='none',
            label='single, s103',
            markeredgecolor='c',
            )

ax.semilogy(ene_s87, num_s87,
            linestyle=' ',
            marker='D',markersize=4,
            # mfc='b',
            mfc='none',
            label='single, s87',
            markeredgecolor='b',
            )

# ax.errorbar(exp_energy_B, exp_number_B, 
#             yerr=exp_number_B_yerr, 
#             xerr=exp_energy_B_xerr,
#             fmt='.b',markersize=4,
#             mfc='none',
#             ecolor='b',elinewidth=1.0,
#             capsize=2.0, capthick = 1.0,
#             label='Exp. w/ B'
#            )
# ax.set_yscale('log')

# noise baseline

energy_range = np.linspace(1,400)
# noise = 33249*(energy_range*1e-3)**(-2.6215)
# noise_de = noise[:-1]/((energy_range[1:]-energy_range[0:-1])/1e0)
noise_base = 10**(-0.0083*energy_range+10.3)
# plt.loglog(energy_range[:-1], noise_de*1e2, '--c', label='noise')
ax.semilogy(energy_range, noise_base, ':k', label='noise')

# ax.semilogy(ekin0*1e3,num0*1e12,'--b',label='Sim. Single at {:.1f} ns'.format(t_end0*1e9))
# ax.semilogy(ekin1*1e3,num1*1e12,'-r',label='Sim. double at {:.1f} ns'.format(t_end1*1e9))

ax.semilogy(ekin0*1e3,num0*8e10,'--b',label='Sim. Single')
ax.semilogy(ekin1*1e3,num1*3e11,'-r',label='Sim. double')

# y1=10.^(-0.0083.*x1+10.3);

ax.set_xlim(0,400)
ax.set_ylim(1e7,1e12)

ax.set_xlabel('Energy (keV)')
ax.set_ylabel(r'dN/dE/d$\Omega$ (No./MeV/sr)') # dN/(dE.dOmega) (part/(MeV.sr))
ax.legend(fancybox=False, reverse=False, frameon=False)
fig.set_size_inches(width, height)
fig.tight_layout()


NameError: name 'ekin0' is not defined

In [ ]:
fig.savefig('/Users/yao/Desktop/spec_exp_sim.pdf')

In [27]:
# experiment

width  = 3.487 * 2
height = width / 1.618 * 1.2

fig, ax = plt.subplots()
fig.subplots_adjust(left=.15, bottom=.16, right=.99, top=.97)

ax.semilogy(ene_s98, num_s98,
            linestyle=' ',
            marker='o',markersize=3,mfc='orange',
            label='double, s98',
            markeredgecolor='orange',
            )

ax.semilogy(ene_s86, num_s86,
            linestyle=' ',
            marker='s',markersize=3,mfc='red',
            label='double, s86',
            markeredgecolor='red',
            )

# ax.semilogy(ene_s94, num_s94,
#             linestyle=' ',
#             marker='^',markersize=4,mfc='none',
#             label='s94',
#             markeredgecolor='m',
#             )

ax.semilogy(ene_s103, num_s103,
            linestyle=' ',
            marker='X',markersize=5,
            # mfc='c',
            mfc='none',
            label='single, s103',
            markeredgecolor='c',
            )

ax.semilogy(ene_s87, num_s87,
            linestyle=' ',
            marker='D',markersize=4,
            # mfc='b',
            mfc='none',
            label='single, s87',
            markeredgecolor='b',
            )

# ax.errorbar(exp_energy_B, exp_number_B, 
#             yerr=exp_number_B_yerr, 
#             xerr=exp_energy_B_xerr,
#             fmt='.b',markersize=4,
#             mfc='none',
#             ecolor='b',elinewidth=1.0,
#             capsize=2.0, capthick = 1.0,
#             label='Exp. w/ B'
#            )
# ax.set_yscale('log')

# noise baseline

energy_range = np.linspace(1,400)
# noise = 33249*(energy_range*1e-3)**(-2.6215)
# noise_de = noise[:-1]/((energy_range[1:]-energy_range[0:-1])/1e0)
noise_base = 10**(-0.0083*energy_range+10.3)
# plt.loglog(energy_range[:-1], noise_de*1e2, '--c', label='noise')
ax.semilogy(energy_range, noise_base, ':k', label='noise')

# ax.semilogy(ekin0*1e3,num0*1e12,'--b',label='Sim. Single at {:.1f} ns'.format(t_end0*1e9))
# ax.semilogy(ekin1*1e3,num1*1e12,'-r',label='Sim. double at {:.1f} ns'.format(t_end1*1e9))

# ax.semilogy(ekin0*1e3,num0*8e10,'--b',label='Sim. Single at 4 ns')
# ax.semilogy(ekin1*1e3,num1*3e11,'-r',label='Sim. double at 4 ns')

ax.semilogy(ekin2*1e3,num2*8e10,'--c',label='Sim. Single at 3 ns')
ax.semilogy(ekin3*1e3,num3*8e10,'-m',label='Sim. double at 3 ns')

# ax.semilogy(ekin4*1e3,num4*8e10,'--g',label='Sim. Single at 2.3 ns')
# ax.semilogy(ekin5*1e3,num5*3e11,'-k',label='Sim. double at 2.3 ns')

# y1=10.^(-0.0083.*x1+10.3);

ax.set_xlim(0,600)
ax.set_ylim(1e7,1e12)

ax.set_xlabel('Energy (keV)')
ax.set_ylabel(r'dN/dE/d$\Omega$ (No./MeV/sr)') # dN/(dE.dOmega) (part/(MeV.sr))
ax.legend(fancybox=False, reverse=False, frameon=False)
fig.set_size_inches(width, height)
fig.tight_layout()


In [68]:
fig.savefig('/Users/yao/Desktop/spectra_times.pdf')

In [ ]:
datasets = np.array([num_s98, num_s86, num_s94])
average = datasets.mean(axis=0)
std_dev = datasets.std(axis=0)
plt.errorbar(ene_s98, average, yerr=std_dev,
            fmt='.b',markersize=4,
            linestyle='none')
plt.yscale('log')
plt.xlim([0,400])
plt.show()


In [34]:
# compare the double shock colliding case with 7 bars vs. 4 bars


num = 77
time_snap = S1.ParticleBinning(2).getTimesteps()[num] # 2.3 ns
print(S1.ParticleBinning(2,units=['ns']).getTimes()[num])

ekin1, num1, t_end1 = spect_load_1d_iter(wkdir[1], time_snap, 2, 0.0, Lx)
ekin0, num0, t_end0 = spect_load_1d_iter(wkdir[0], time_snap, 2, 0.0, Lx)

2.276329474387547
Loaded simulation '/Users/yao/Desktop/Data/DS_10_r0/'
Loaded simulation '/Users/yao/Desktop/Data/DS_10_r1/'
Scanning for Scalar diagnostics
Scanning for Field diagnostics
Scanning for Probe diagnostics
Scanning for ParticleBinning diagnostics
Scanning for RadiationSpectrum diagnostics
Scanning for Performance diagnostics
Scanning for Screen diagnostics
Scanning for Tracked particle diagnostics
Scanning for new particle diagnostics
Loaded simulation '/Users/yao/Desktop/Data/DS_9_r0/'
Loaded simulation '/Users/yao/Desktop/Data/DS_9_r1/'
Scanning for Scalar diagnostics
Scanning for Field diagnostics
Scanning for Probe diagnostics
Scanning for ParticleBinning diagnostics
Scanning for RadiationSpectrum diagnostics
Scanning for Performance diagnostics
Scanning for Screen diagnostics
Scanning for Tracked particle diagnostics
Scanning for new particle diagnostics


In [36]:
num = 115
time_snap = S1.ParticleBinning(2).getTimesteps()[num] 
print(S1.ParticleBinning(2,units=['ns']).getTimes()[num])

ekin3, num3, t_end3 = spect_load_1d_iter(wkdir[1], time_snap, 2, 0.0, Lx)
ekin2, num2, t_end2 = spect_load_1d_iter(wkdir[0], time_snap, 2, 0.0, Lx)

3.3997128513580246
Loaded simulation '/Users/yao/Desktop/Data/DS_10_r0/'
Loaded simulation '/Users/yao/Desktop/Data/DS_10_r1/'
Scanning for Scalar diagnostics
Scanning for Field diagnostics
Scanning for Probe diagnostics
Scanning for ParticleBinning diagnostics
Scanning for RadiationSpectrum diagnostics
Scanning for Performance diagnostics
Scanning for Screen diagnostics
Scanning for Tracked particle diagnostics
Scanning for new particle diagnostics
Loaded simulation '/Users/yao/Desktop/Data/DS_9_r0/'
Loaded simulation '/Users/yao/Desktop/Data/DS_9_r1/'
Scanning for Scalar diagnostics
Scanning for Field diagnostics
Scanning for Probe diagnostics
Scanning for ParticleBinning diagnostics
Scanning for RadiationSpectrum diagnostics
Scanning for Performance diagnostics
Scanning for Screen diagnostics
Scanning for Tracked particle diagnostics
Scanning for new particle diagnostics


In [48]:
num = 100
time_snap = S1.ParticleBinning(2).getTimesteps()[num] 
print(S1.ParticleBinning(2,units=['ns']).getTimes()[num])

ekin5, num5, t_end5 = spect_load_1d_iter(wkdir[1], time_snap, 2, 0.0, Lx)
ekin4, num4, t_end4 = spect_load_1d_iter(wkdir[0], time_snap, 2, 0.0, Lx)

2.9562720446591517
Loaded simulation '/Users/yao/Desktop/Data/DS_10_r0/'
Loaded simulation '/Users/yao/Desktop/Data/DS_10_r1/'
Scanning for Scalar diagnostics
Scanning for Field diagnostics
Scanning for Probe diagnostics
Scanning for ParticleBinning diagnostics
Scanning for RadiationSpectrum diagnostics
Scanning for Performance diagnostics
Scanning for Screen diagnostics
Scanning for Tracked particle diagnostics
Scanning for new particle diagnostics
Loaded simulation '/Users/yao/Desktop/Data/DS_9_r0/'
Loaded simulation '/Users/yao/Desktop/Data/DS_9_r1/'
Scanning for Scalar diagnostics
Scanning for Field diagnostics
Scanning for Probe diagnostics
Scanning for ParticleBinning diagnostics
Scanning for RadiationSpectrum diagnostics
Scanning for Performance diagnostics
Scanning for Screen diagnostics
Scanning for Tracked particle diagnostics
Scanning for new particle diagnostics


In [49]:
# experiment

width  = 3.487 * 2
height = width / 1.618 * 1.2

fig, ax = plt.subplots()
fig.subplots_adjust(left=.15, bottom=.16, right=.99, top=.97)

ax.semilogy(ene_s98, num_s98,
            linestyle=' ',
            marker='o',markersize=3,mfc='orange',
            label='double, s98, 7 bars',
            markeredgecolor='orange',
            )

ax.semilogy(ene_s86, num_s86,
            linestyle=' ',
            marker='s',markersize=3,mfc='red',
            label='double, s86, 7 bars',
            markeredgecolor='red',
            )

ax.semilogy(ene_s94, num_s94,
            linestyle=' ',
            marker='^',markersize=4,mfc='none',
            label='double, s94, 5 bars',
            markeredgecolor='m',
            )

ax.semilogy(ene_s97, num_s97,
            linestyle=' ',
            marker='D',markersize=4,mfc='none',
            label='double, s97, 4 bars',
            markeredgecolor='b',
            )

# ax.semilogy(ene_s103, num_s103,
#             linestyle=' ',
#             marker='X',markersize=5,
#             # mfc='c',
#             mfc='none',
#             label='single, s103',
#             markeredgecolor='c',
#             )

# ax.semilogy(ene_s87, num_s87,
#             linestyle=' ',
#             marker='D',markersize=4,
#             # mfc='b',
#             mfc='none',
#             label='single, s87',
#             markeredgecolor='b',
#             )

# ax.errorbar(exp_energy_B, exp_number_B, 
#             yerr=exp_number_B_yerr, 
#             xerr=exp_energy_B_xerr,
#             fmt='.b',markersize=4,
#             mfc='none',
#             ecolor='b',elinewidth=1.0,
#             capsize=2.0, capthick = 1.0,
#             label='Exp. w/ B'
#            )
# ax.set_yscale('log')

# noise baseline

energy_range = np.linspace(1,500)
# noise = 33249*(energy_range*1e-3)**(-2.6215)
# noise_de = noise[:-1]/((energy_range[1:]-energy_range[0:-1])/1e0)
noise_base = 10**(-0.0083*energy_range+10.3)
# plt.loglog(energy_range[:-1], noise_de*1e2, '--c', label='noise')
ax.semilogy(energy_range, noise_base, ':k', label='noise')

# ax.semilogy(ekin0*1e3,num0*1e12,'--b',label='Sim. Single at {:.1f} ns'.format(t_end0*1e9))
# ax.semilogy(ekin1*1e3,num1*1e12,'-r',label='Sim. double at {:.1f} ns'.format(t_end1*1e9))

ax.semilogy(ekin0*1e3,num0*8e10*5,'-r',label='Sim. double, at 7 bars, at 2.3 ns')
ax.semilogy(ekin1*1e3,num1*8e10*5,'--b',lw=2.0,label='Sim. double, at 3.5 bars, at 2.3 ns')

ax.semilogy(ekin2*1e3,num2*8e10*5,'-m',label='Sim. double, at 7 bars, at 3.3 ns')
ax.semilogy(ekin3*1e3,num3*8e10*5,'--c',lw=2.0,label='Sim. double, at 3.5 bars, at 3.3 ns')

ax.semilogy(ekin4*1e3,num4*8e10*5,'-k',label='Sim. double, at 7 bars, at 2.9 ns')
ax.semilogy(ekin5*1e3,num5*8e10*5,'--y',lw=2.0,label='Sim. double, at 3.5 bars, at 2.9 ns')


# ax.semilogy(ekin2*1e3,num2*8e10,'--c',label='Sim. Single at 3 ns')
# ax.semilogy(ekin3*1e3,num3*3e11,'-m',label='Sim. double at 3 ns')

# ax.semilogy(ekin4*1e3,num4*8e10,'--g',label='Sim. Single at 2.3 ns')
# ax.semilogy(ekin5*1e3,num5*3e11,'-k',label='Sim. double at 2.3 ns')

# y1=10.^(-0.0083.*x1+10.3);

ax.set_xlim(0,500)
ax.set_ylim(1e6,1e12)

ax.set_xlabel('Energy (keV)')
ax.set_ylabel(r'dN/dE/d$\Omega$ (No./MeV/sr)') # dN/(dE.dOmega) (part/(MeV.sr))
ax.legend(fancybox=False, reverse=False, frameon=False)
fig.set_size_inches(width, height)
fig.tight_layout()


In [47]:
fig.savefig('/Users/yao/Desktop/spectra_pressure2.pdf')

In [ ]:
I_0 = 1.9e22
lmd = 0.815

In [ ]:
a_0   = np.sqrt(I_0*lmd**2/1.37e18)

In [ ]:
a_0

In [17]:
# energy spectra with errorbars

# averaged over 6 shots

data_directory = '/Users/yao/Nextcloud/PROJECTS/Vulcan/RAL_August2023/'
data_file_double = 'double_spectra_combined_sigma2.txt'
data_file_single = 'single_spectra_combined.txt'

ene_exp_db = np.loadtxt(data_directory+data_file_double,usecols=0) # in keV
num_exp_db = np.loadtxt(data_directory+data_file_double,usecols=1) # in part/(MeV.sr)
err_exp_db = np.loadtxt(data_directory+data_file_double,usecols=2) # in keV

ene_exp_sg = np.loadtxt(data_directory+data_file_single,usecols=0) # in keV
num_exp_sg = np.loadtxt(data_directory+data_file_single,usecols=1) # in part/(MeV.sr)
err_exp_sg = np.loadtxt(data_directory+data_file_single,usecols=2) # in keV


In [8]:
S1.ParticleBinning(2).getTimesteps().size

146

In [45]:
# num = 130 # 4 ns
num = 130 # last timestep for DS_v2500_r0
time_snap = S1.ParticleBinning(2).getTimesteps()[num]
time_ns = S1.ParticleBinning(2,units=['ns']).getTimes()[num]
print(time_ns)

ekin1, num1, t_end1 = spect_load_1d_iter(wkdir[1], time_snap, 2, 0.0, Lx)
ekin0, num0, t_end0 = spect_load_1d_iter(wkdir[0], time_snap, 2, 0.0, Lx)

3.8431536580568975
Loaded simulation '/Users/yao/Desktop/Data/v2500/DS_11_v2500_r0/'
Loaded simulation '/Users/yao/Desktop/Data/v2500/DS_11_v2500_r1/'
Scanning for Scalar diagnostics
Scanning for Field diagnostics
Scanning for Probe diagnostics
Scanning for ParticleBinning diagnostics
Scanning for RadiationSpectrum diagnostics
Scanning for Performance diagnostics
Scanning for Screen diagnostics
Scanning for Tracked particle diagnostics
Scanning for new particle diagnostics
Loaded simulation '/Users/yao/Desktop/Data/v2500/SS_11_v2500_r0/'
Loaded simulation '/Users/yao/Desktop/Data/v2500/SS_11_v2500_r1/'
Scanning for Scalar diagnostics
Scanning for Field diagnostics
Scanning for Probe diagnostics
Scanning for ParticleBinning diagnostics
Scanning for RadiationSpectrum diagnostics
Scanning for Performance diagnostics
Scanning for Screen diagnostics
Scanning for Tracked particle diagnostics
Scanning for new particle diagnostics


In [46]:
width  = 3.14 *1.5 # single column, 8cm
height = width
fig, ax = plt.subplots()

plt.ticklabel_format(axis='both', style='sci',useMathText=True)

fig.subplots_adjust(left=.2, bottom=.2, right=.9, top=.9)

# ax.set_xscale('log')
ax.set_yscale('log')

ax.errorbar(ene_exp_db[0:-1:8], num_exp_db[0:-1:8], yerr=err_exp_db[0:-1:8], 
            fmt='or',markersize=3,
            ecolor='r',elinewidth=1.0,
            # capsize=2.0, capthick = 1.0,
            label='Exp. Data: double')

ax.errorbar(ene_exp_sg[0:-1:4], num_exp_sg[0:-1:4], yerr=err_exp_sg[0:-1:4], 
            fmt='sb',markersize=3,
            ecolor='b',elinewidth=1.0,
            # capsize=2.0, capthick = 1.0,
            label='Exp. Data: single')

# ax.plot(ekin3, num3, '-k',  label='Bz=0', lw=1.0)
ax.plot(ekin0*1e3, num0*7e11, '--b',  label='Sim. Single at {:.1f} ns'.format(time_ns), lw=1.5)
ax.plot(ekin1*1e3, num1*3e12, '--r',  label='Sim. Double at {:.1f} ns'.format(time_ns), lw=1.5)
# ax.plot(ekin2, num2, '-g',  label='Bz=17T', lw=1.0)
# ax.plot(ekin0, num0, '-y',  label='Shock Width=di~200um', lw=1.0)


ax.tick_params(axis='both',which='major', direction='out',labelsize=12)
ax.minorticks_off()

ax.set_xlabel(r'$E_{p}$ (keV)',fontsize=12)
# ax.set_ylabel(r'$E\frac{dN}{dE}\frac{1}{N}$',fontsize=12)
ax.set_ylabel(r'Part./(keV$\cdot$sr)',fontsize=12)


ax.set_xlim([20, 400])
# formatter = ScalarFormatter()
# formatter.set_scientific(False)
# ax.xaxis.set_major_formatter(formatter)
# ax.set_xticks([0.02, 0.05, 0.08])
# ax.set_xticklabels([0.01, 0.05, 0.10],fontsize=8)


ax.set_ylim([1e7, 1e12])
# ax.set_yticks([1, 0.01, 0.0001])

def func(x,kbT):
    edrift = 0.
    return x*np.sqrt(x)*np.exp(-(x-edrift)**2/kbT) 

index = (ekin0 < 300/1e3)*(ekin0 > 15.0/1e3)
# popt, pcov = curve_fit(func, ekin0[index], num0[index])
# print(popt,pcov)
# y2 = func(ekin0[index], 100.0/1e6)
# ax.plot(ekin0[index], y2*4e3, 'r--',label='100eV')
y3 = func(ekin0[index], 250.0/1e6)
# ax.semilogy(ekin0[index]*1e3, y3*1e15, 'c--',lw=1.0, label='Thermal 250 eV')

energy_range = np.linspace(1,500)
# noise = 33249*(energy_range*1e-3)**(-2.6215)
# noise_de = noise[:-1]/((energy_range[1:]-energy_range[0:-1])/1e0)
noise_base = 10**(-0.0083*energy_range+10.3)
# plt.loglog(energy_range[:-1], noise_de*1e2, '--c', label='noise')
ax.semilogy(energy_range, noise_base, ':k', lw=1.0,label='noise')

leg = ax.legend(loc='best', numpoints=1, fancybox=False, fontsize=8, frameon=False)
leg._legend_box.align = "right"
# ax.grid(which='both')
fig.set_size_inches(width, height)
plt.show()


In [47]:
fig.savefig('/Users/yao/Desktop/'+'spec_v2500_'+str(num)+'.pdf',bbox_inches='tight',dpi=600)

In [19]:
def save_spectrum(num):
    width  = 3.14 *1.5 # single column, 8cm
    height = width
    plt.ioff()
    fig, ax = plt.subplots()

    plt.ticklabel_format(axis='both', style='sci',useMathText=True)

    fig.subplots_adjust(left=.2, bottom=.2, right=.9, top=.9)

    # ax.set_xscale('log')
    ax.set_yscale('log')

    ax.errorbar(ene_exp_db[0:-1:8], num_exp_db[0:-1:8], yerr=err_exp_db[0:-1:8], 
                fmt='or',markersize=3,
                ecolor='r',elinewidth=1.0,
                # capsize=2.0, capthick = 1.0,
                label='Exp. Data: double')

    ax.errorbar(ene_exp_sg[0:-1:4], num_exp_sg[0:-1:4], yerr=err_exp_sg[0:-1:4], 
                fmt='sb',markersize=3,
                ecolor='b',elinewidth=1.0,
                # capsize=2.0, capthick = 1.0,
                label='Exp. Data: single')

    # ax.plot(ekin3, num3, '-k',  label='Bz=0', lw=1.0)
    ax.plot(ekin0*1e3, num0*7e11, '--b',  label='Sim. Single at {:.1f} ns'.format(time_ns), lw=1.5)
    ax.plot(ekin1*1e3, num1*3e12, '--r',  label='Sim. Double at {:.1f} ns'.format(time_ns), lw=1.5)
    # ax.plot(ekin2, num2, '-g',  label='Bz=17T', lw=1.0)
    # ax.plot(ekin0, num0, '-y',  label='Shock Width=di~200um', lw=1.0)


    ax.tick_params(axis='both',which='major', direction='out',labelsize=12)
    ax.minorticks_off()

    ax.set_xlabel(r'$E_{p}$ (keV)',fontsize=12)
    # ax.set_ylabel(r'$E\frac{dN}{dE}\frac{1}{N}$',fontsize=12)
    ax.set_ylabel(r'Part./(keV$\cdot$sr)',fontsize=12)


    ax.set_xlim([20, 400])
    # formatter = ScalarFormatter()
    # formatter.set_scientific(False)
    # ax.xaxis.set_major_formatter(formatter)
    # ax.set_xticks([0.02, 0.05, 0.08])
    # ax.set_xticklabels([0.01, 0.05, 0.10],fontsize=8)


    ax.set_ylim([1e7, 1e12])
    # ax.set_yticks([1, 0.01, 0.0001])

    def func(x,kbT):
        edrift = 0.
        return x*np.sqrt(x)*np.exp(-(x-edrift)**2/kbT) 

    index = (ekin0 < 300/1e3)*(ekin0 > 15.0/1e3)
    # popt, pcov = curve_fit(func, ekin0[index], num0[index])
    # print(popt,pcov)
    # y2 = func(ekin0[index], 100.0/1e6)
    # ax.plot(ekin0[index], y2*4e3, 'r--',label='100eV')
    y3 = func(ekin0[index], 250.0/1e6)
    # ax.semilogy(ekin0[index]*1e3, y3*1e15, 'c--',lw=1.0, label='Thermal 250 eV')

    energy_range = np.linspace(1,500)
    # noise = 33249*(energy_range*1e-3)**(-2.6215)
    # noise_de = noise[:-1]/((energy_range[1:]-energy_range[0:-1])/1e0)
    noise_base = 10**(-0.0083*energy_range+10.3)
    # plt.loglog(energy_range[:-1], noise_de*1e2, '--c', label='noise')
    ax.semilogy(energy_range, noise_base, ':k', lw=1.0,label='noise')

    leg = ax.legend(loc='best', numpoints=1, fancybox=False, fontsize=8, frameon=False)
    leg._legend_box.align = "right"
    # ax.grid(which='both')
    fig.set_size_inches(width, height)
    # plt.show()
    fig.savefig('/Users/yao/Desktop/spec_v2000/'+'spec_v2000_'+str(num)+'.pdf',bbox_inches='tight',dpi=600)

In [20]:
## save a series of energy spectrum to check their evolution
# num = 130 # 4 ns
# num = np.linspace(120,144,13)
# num = 130 # last timestep for DS_v2500_r0
for num in range(44):
    num = num*2+60
    time_snap = S1.ParticleBinning(2).getTimesteps()[int(num)]
    time_ns = S1.ParticleBinning(2,units=['ns']).getTimes()[int(num)]
    print(time_ns)

    ekin1, num1, t_end1 = spect_load_1d_iter(wkdir[1], time_snap, 2, 0.0, Lx)
    ekin0, num0, t_end0 = spect_load_1d_iter(wkdir[0], time_snap, 2, 0.0, Lx)

    save_spectrum(num)
    

1.773763226795491
Loaded simulation '/Users/yao/Desktop/Data/DS_12_v2000_r0/'
Loaded simulation '/Users/yao/Desktop/Data/DS_12_v2000_r1/'
Scanning for Scalar diagnostics
Scanning for Field diagnostics
Scanning for Probe diagnostics
Scanning for ParticleBinning diagnostics
Scanning for RadiationSpectrum diagnostics
Scanning for Performance diagnostics
Scanning for Screen diagnostics
Scanning for Tracked particle diagnostics
Scanning for new particle diagnostics
Loaded simulation '/Users/yao/Desktop/Data/SS_12_v2000_r0/'
Loaded simulation '/Users/yao/Desktop/Data/SS_12_v2000_r1/'
Scanning for Scalar diagnostics
Scanning for Field diagnostics
Scanning for Probe diagnostics
Scanning for ParticleBinning diagnostics
Scanning for RadiationSpectrum diagnostics
Scanning for Performance diagnostics
Scanning for Screen diagnostics
Scanning for Tracked particle diagnostics
Scanning for new particle diagnostics
1.8328886676886742
Loaded simulation '/Users/yao/Desktop/Data/DS_12_v2000_r0/'
Loaded si

/var/folders/2t/97rc3fl92tg15k2l_4sk5hsh0000gn/T/ipykernel_19948/1562755779.py:5: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`). Consider using `matplotlib.pyplot.close()`.
  fig, ax = plt.subplots()


Loaded simulation '/Users/yao/Desktop/Data/DS_12_v2000_r0/'
Loaded simulation '/Users/yao/Desktop/Data/DS_12_v2000_r1/'
Scanning for Scalar diagnostics
Scanning for Field diagnostics
Scanning for Probe diagnostics
Scanning for ParticleBinning diagnostics
Scanning for RadiationSpectrum diagnostics
Scanning for Performance diagnostics
Scanning for Screen diagnostics
Scanning for Tracked particle diagnostics
Scanning for new particle diagnostics
Loaded simulation '/Users/yao/Desktop/Data/SS_12_v2000_r0/'
Loaded simulation '/Users/yao/Desktop/Data/SS_12_v2000_r1/'
Scanning for Scalar diagnostics
Scanning for Field diagnostics
Scanning for Probe diagnostics
Scanning for ParticleBinning diagnostics
Scanning for RadiationSpectrum diagnostics
Scanning for Performance diagnostics
Scanning for Screen diagnostics
Scanning for Tracked particle diagnostics
Scanning for new particle diagnostics
2.897146603765969
Loaded simulation '/Users/yao/Desktop/Data/DS_12_v2000_r0/'
Loaded simulation '/Users/ya

IndexError: index 146 is out of bounds for axis 0 with size 146

: 

In [56]:
int(np.linspace(120,144,13))

TypeError: only length-1 arrays can be converted to Python scalars

In [ ]:
# for pressure of 4 bars H2
x_data = np.array([3.0,   5.0,   6.0,   7.0,   8.0]) # time in ns
y_data = np.array([9.51, 13.97, 15.45, 18.38, 20.68]) # size (diameter) in mm

In [ ]:
## Piston and shock front position vs. time -> for velocities
## data from Julien Fuchs in the file "rough analysis p-rad shock"

time_ns = np.array([0.5, 1.0, 2.0, 3.0, 4.0])

shock_front_B1_mm  = np.array([1.63, 3.27, 3.55, 3.92, 5.03])
shock_front_B6_mm  = np.array([0.0,  3.42, 4.12, 5.03, 5.53])

piston_front_B1_mm = np.array([1.19, 2.46, 2.83, 3.28, 4.73])
piston_front_B6_mm = np.array([1.15, 2.28, 3.65, 4.36, 4.11])



In [ ]:
width  = 3.487 * 1.3
height = width / 1.618 * 1.2

fig, ax = plt.subplots()
fig.subplots_adjust(left=.15, bottom=.16, right=.99, top=.97)

ax.plot(time_ns, piston_front_B1_mm, '^b',
         markersize=6,
        label='Piston B1')
ax.plot(time_ns, piston_front_B6_mm, 'ob', 
        mfc='None',markersize=6,
        label='Piston B6')

ax.plot(time_ns, shock_front_B1_mm, '^r', 
        markersize=6,
        label='Shock B1')
ax.plot(time_ns[1:], shock_front_B6_mm[1:], 'or', 
        mfc='None',markersize=6,
        label='Shock B6')

time_1st = np.linspace(0.3, 1.2, 10)
time_2nd = np.linspace(0.8, 4.2, 20)

ax.plot(time_2nd, 0.75*time_2nd+2.5, '--c', label='V: 750 km/s')
ax.plot(time_1st , 3.1*time_1st +0.1, '--m', label='V: 3100 km/s')

ax.set_xlim(0,4.5)
ax.set_ylim(0,6)

ax.set_xlabel('Time (ns)')
ax.set_ylabel('Distance (mm)') 
ax.legend(fancybox=False, reverse=True, frameon=False)
fig.set_size_inches(width, height)
fig.tight_layout()

In [ ]:
fig.savefig('/Users/yao/Desktop/velocities.pdf')

In [ ]:
3.33 / 4.

In [123]:
xx = np.linspace(0,100,100)
yy = np.exp(-xx)

plt.loglog(xx,yy)
plt.ylim(1e-4,2)

(0.0001, 2)